## Introdução

Este notebook tem como objetivo conhecer os conceitos básicos de Spark(pyspark) e fazer uma pequena comparação com a API do Pandas.  ë importante salientar que a sintax embora parecida a Pandas, não é exatamente igual e poderá as suas diferenças na sua construção. 

Outro característica  importante é capacidade de computo distribuído da qual carece de Pandas(python). esta diferença, como foi visto na parte teórica, contempla a criação de partições, criação  um plano lógico, e a execução do plano físico. Cabe relembrar que estes planos estão criados em forma de DAG ( Direct Acyclic Graph).

finalmente será explorado os conceitos de lazy computation, Transformations and Actions. 

Sendo que estamos a utilizar Databricks para as nossas aulas, Todos as tabelas ou dataframes utilizados y criados estarão materializados no DBFS (DataBricks File System) que é um sistema de armazenamento proprietário da databricks mas que no fundo contempla o conceito deDBS(Diastribuited Fiel System)

Para mais informação sobre DBFS [DBFS](https://docs.databricks.com/user-guide/dbfs-databricks-file-system.html)

Este notebook está escrito em **Python** e todas as células assumirão está linguagem de programação como a principal. poderá ser usado outro tipo de linguagem que seja suportado pela API de Spark isto quer dizer Python, Scala, SQL e R. para trocar basta utilizar o comando `%LANGUAGE` ao inicio de cada una das células

Vamos Criar Um DataFrame desde um dos tipo de estructuras de Python

# 0. Desenferrujar os conceitos de SQL e de Pandas

In [0]:
import numpy as np
from datetime import datetime, date
import pandas as pd
import string
import random

In [0]:
rows = 100

df_ints = pd.DataFrame(np.random.randint(0,rows,size=(rows, 4)), columns=list('ABCD'))

def id_generator(size=4, chars=string.ascii_uppercase + string.digits):
    return ''.join(random.choice(chars) for _ in range(size))

df_strings = np.array([id_generator() for i in range(2*rows)]).reshape(-1,2)
df_strings = pd.DataFrame(df_strings)

0.1 selecione as colunas B e D do pandas dataframe

In [0]:
df_strings

0 
 1 
 
 
 
 
 0 
 UVBJ 
 HX60 
 
 
 1 
 35ZS 
 A513 
 
 
 2 
 M2OV 
 2EPG 
 
 
 3 
 KALZ 
 RTWO 
 
 
 4 
 SY9C 
 G5YG 
 
 
 ... 
 ... 
 ... 
 
 
 95 
 CGN6 
 MKW8 
 
 
 96 
 DYDZ 
 NW17 
 
 
 97 
 XM9E 
 0FAC 
 
 
 98 
 5X4O 
 QVIU 
 
 
 99 
 3CEA 
 81LI 
 
 
 
 100 rows × 2 columns

In [0]:
DB = df_strings[0:2]
DB

0 
 1 
 
 
 
 
 0 
 UVBJ 
 HX60 
 
 
 1 
 35ZS 
 A513

0.2 selecione toda linhas onde A e maior de 65

---------------------------------------------------------------------------
TypeError                                 Traceback (most recent call last)
File <command-169419913273320>:1
----> 1 A65 = df_strings[0] > 65
      2 A65

File /databricks/python/lib/python3.9/site-packages/pandas/core/ops/common.py:70, in _unpack_zerodim_and_defer.<locals>.new_method(self, other)
     66             return NotImplemented
     68 other = item_from_zerodim(other)
---> 70 return method(self, other)

File /databricks/python/lib/python3.9/site-packages/pandas/core/arraylike.py:56, in OpsMixin.__gt__(self, other)
     54 @unpack_zerodim_and_defer("__gt__")
     55 def __gt__(self, other):
---> 56     return self._cmp_method(other, operator.gt)

File /databricks/python/lib/python3.9/site-packages/pandas/core/series.py:5623, in Series._cmp_method(self, other, op)
   5620 rvalues = extract_array(other, extract_numpy=True, extract_range=True)
   5622 with np.errstate(all="ignore"):
-> 5623     res_value

# 1. Introduction to PySpark

Que é o primero que se faz quando se compra um maquina de lavar roupa?. 

Ler o manual de instruções.

https://spark.apache.org/docs/latest/api/python/reference/index.html

DataFrame = operações que afetam o dataframe e devolvem im dataframe

Colunas = operações que afetam as colunas

Funçoes = Funçoes que transformam e afetam maioritariamente colunas

Windows = windows function

Data types = trabalhar com os datatypes dos Spark Dataframes

In [0]:
from pyspark.sql import Row



In [0]:
import pyspark

In [0]:
df = spark.createDataFrame([
    Row(a=1, b=2., c='string1', d=date(2000, 1, 1), e=datetime(2000, 1, 1, 12, 0)),
    Row(a=2, b=3., c='string2', d=date(2000, 2, 1), e=datetime(2000, 1, 2, 12, 0)),
    Row(a=4, b=5., c='string3', d=date(2000, 3, 1), e=datetime(2000, 1, 3, 12, 0)),
   Row(a=4, b=5., c='string3', d=date(2000, 3, 1), e=datetime(2001, 1, 3, 12, 0)),
   Row(a=5, b=5., c='string3', d=date(2000, 3, 1), e=datetime(2002, 1, 3, 12, 0)),
   Row(a=6, b=5., c='string3', d=date(2000, 3, 1), e=datetime(2003, 1, 3, 12, 0)),
   Row(a=7, b=5., c='string3', d=date(2000, 3, 1), e=datetime(2000, 1, 3, 12, 0)),
   Row(a=8, b=5., c='string3', d=date(2000, 3, 1), e=datetime(2016, 1, 8, 12, 0)),
   Row(a=9, b=5., c='string3', d=date(2000, 3, 1), e=datetime(2019, 1, 9, 12, 0)),
   Row(a=10, b=5., c='string3', d=date(2000, 3, 1), e=datetime(2018, 1, 10, 12, 0)),
   Row(a=11, b=5., c='string3', d=date(2000, 3, 1), e=datetime(2021, 1, 12, 12, 0))
])

In [0]:
df

Out[15]: DataFrame[a: bigint, b: double, c: string, d: date, e: timestamp]

In [0]:
display(df)

a b c d e 1 2.0 string1 2000-01-01 2000-01-01T12:00:00.000+0000 2 3.0 string2 2000-02-01 2000-01-02T12:00:00.000+0000 4 5.0 string3 2000-03-01 2000-01-03T12:00:00.000+0000 4 5.0 string3 2000-03-01 2001-01-03T12:00:00.000+0000 5 5.0 string3 2000-03-01 2002-01-03T12:00:00.000+0000 6 5.0 string3 2000-03-01 2003-01-03T12:00:00.000+0000 7 5.0 string3 2000-03-01 2000-01-03T12:00:00.000+0000 8 5.0 string3 2000-03-01 2016-01-08T12:00:00.000+0000 9 5.0 string3 2000-03-01 2019-01-09T12:00:00.000+0000 10 5.0 string3 2000-03-01 2018-01-10T12:00:00.000+0000 11 5.0 string3 2000-03-01 2021-01-12T12:00:00.000+0000

In [0]:
df = spark.createDataFrame([
    Row(a=1, b=2., c='string1', d=date(2000, 1, 1), e=datetime(2000, 1, 1, 12, 0)),
    Row(a=2, b=3., c='string2', d=date(2000, 2, 1), e=datetime(2000, 1, 2, 12, 0)),
    Row(a=4, b=5., c='string3', d=date(2000, 3, 1), e=datetime(2000, 1, 3, 12, 0)),
   Row(a=4, b=5., c='string3', d=date(2000, 3, 1), e=datetime(2001, 1, 3, 12, 0)),
   Row(a=5, b=5., c='string3', d=date(2000, 3, 1), e=datetime(2002, 1, 3, 12, 0)),
   Row(a=6, b=5., c='string3', d=date(2000, 3, 1), e=datetime(2003, 1, 3, 12, 0)),
   Row(a=7, b=5., c='string3', d=date(2000, 3, 1), e=datetime(2000, 1, 3, 12, 0)),
   Row(a=8, b=5., c='string3', d=date(2000, 3, 1), e=datetime(2016, 1, 8, 12, 0)),
   Row(a=9, b=5., c='string3', d=date(2000, 3, 1), e=datetime(2019, 1, 9, 12, 0)),
   Row(a=10, b=5., c='string3', d=date(2000, 3, 1), e=datetime(2018, 1, 10, 12, 0)),
   Row(a=11, b=5., c='string3', d=date(2000, 3, 1), e=datetime(2021, 1, 12, 12, 0))
], schema='a long, b double, c string, d date, e timestamp')

## Visualizar os dados

Para poder visualizar o Dataframe anterior não basta com chamar a variável `df`. Experimentemos

In [0]:
df

Out[6]: DataFrame[a: bigint, b: double, c: string, d: date, e: timestamp]

O resultado de "Chamar" a variável atribuida ao do dataframe(df) só mostrará o schema do dataframe. Isto permite compreender as propiedades do lazy computation, funcionalidade escencial de Spark. Só quando utilizamos uma *Action* é que o realmente o Spark acciona a computação do plano de execução.

para poder ver o resultado (Dataframe) dum plano de execução, de forma colunar, como é feito como o Pandas, é necessário utilizar a ação `show()`. esta ação irá a calcular tudo o que existe no plano execução e dara como resultado so as primeiras linhas do Dataframe. é o equivalente ao `print()` 

para limitar o número de linhas a visualizar basta passar como parámetro o número desejado na função `show()` Ex. `show(2)`

In [0]:
df.show()

+---+---+-------+----------+-------------------+
|  a|  b|      c|         d|                  e|
+---+---+-------+----------+-------------------+
|  1|2.0|string1|2000-01-01|2000-01-01 12:00:00|
|  2|3.0|string2|2000-02-01|2000-01-02 12:00:00|
|  4|5.0|string3|2000-03-01|2000-01-03 12:00:00|
|  4|5.0|string3|2000-03-01|2001-01-03 12:00:00|
|  5|5.0|string3|2000-03-01|2002-01-03 12:00:00|
|  6|5.0|string3|2000-03-01|2003-01-03 12:00:00|
|  7|5.0|string3|2000-03-01|2000-01-03 12:00:00|
|  8|5.0|string3|2000-03-01|2016-01-08 12:00:00|
|  9|5.0|string3|2000-03-01|2019-01-09 12:00:00|
| 10|5.0|string3|2000-03-01|2018-01-10 12:00:00|
| 11|5.0|string3|2000-03-01|2021-01-12 12:00:00|
+---+---+-------+----------+-------------------+



In [0]:
df.show(1)

+---+---+-------+----------+-------------------+
|  a|  b|      c|         d|                  e|
+---+---+-------+----------+-------------------+
|  1|2.0|string1|2000-01-01|2000-01-01 12:00:00|
+---+---+-------+----------+-------------------+
only showing top 1 row



Podemos visualizar os dados de forma vertical

In [0]:
df.show(1, vertical=True)

-RECORD 0------------------
 a | 1 
 b | 2.0 
 c | string1 
 d | 2000-01-01 
 e | 2000-01-01 12:00:00 
only showing top 1 row

Se não quisermos truncar os resultado `...` e que apareçan reticências

In [0]:
df.show(2, truncate=False,vertical=True) 

-RECORD 0------------------
 a   | 1                   
 b   | 2.0                 
 c   | string1             
 d   | 2000-01-01          
 e   | 2000-01-01 12:00:00 
-RECORD 1------------------
 a   | 2                   
 b   | 3.0                 
 c   | string2             
 d   | 2000-02-01          
 e   | 2000-01-02 12:00:00 
only showing top 2 rows



Muitas das vezes é importante definir o schema do dataframe e quais são os *data types* para cada uma das columnas.  os datatypes são consistentes e inmutáveis, isto quer dizer que se no schema uma coluna é definida como uma String, não poderemos escrever um Float. definir o schema é fulcral quando no processo de ETL *Extract Transforamtion and Load* pretende-se ter um resultado controlado. Ex. uma aplicação Spark não poderá aplicar um operação REGEX *Regular Expression* Sobre uma datatype Diferente a `String`

para poder conhecer o schema do dataframe, seja qual for o método de ingestão dos dados, basta com usar a fução `printSchema()`

In [0]:
df.printSchema()

root
 |-- a: long (nullable = true)
 |-- b: double (nullable = true)
 |-- c: string (nullable = true)
 |-- d: date (nullable = true)
 |-- e: timestamp (nullable = true)



#### Collect() take(), tail(), show()?

`show()`: mostra o resultado esperado dos dados e forma tabular

`collect()`: processa todo o plano de execução e coleita todos os dados que foram processados de foram dsitribuida e os traz a sessão local de python. Isto pode criar falta e memória na sessão local, devido a sua infraestructuera limitada, não se recomenda utilizar o collect para visualização preliminar dos resultados

`take()` or ``tail()``:  retorna um dataframe como o número de linhas que é desajado seja pelo inicio ou pelo fim

In [0]:
df.collect()

Out[12]: [Row(a=1, b=2.0, c='string1', d=datetime.date(2000, 1, 1), e=datetime.datetime(2000, 1, 1, 12, 0)),
 Row(a=2, b=3.0, c='string2', d=datetime.date(2000, 2, 1), e=datetime.datetime(2000, 1, 2, 12, 0)),
 Row(a=4, b=5.0, c='string3', d=datetime.date(2000, 3, 1), e=datetime.datetime(2000, 1, 3, 12, 0)),
 Row(a=4, b=5.0, c='string3', d=datetime.date(2000, 3, 1), e=datetime.datetime(2001, 1, 3, 12, 0)),
 Row(a=5, b=5.0, c='string3', d=datetime.date(2000, 3, 1), e=datetime.datetime(2002, 1, 3, 12, 0)),
 Row(a=6, b=5.0, c='string3', d=datetime.date(2000, 3, 1), e=datetime.datetime(2003, 1, 3, 12, 0)),
 Row(a=7, b=5.0, c='string3', d=datetime.date(2000, 3, 1), e=datetime.datetime(2000, 1, 3, 12, 0)),
 Row(a=8, b=5.0, c='string3', d=datetime.date(2000, 3, 1), e=datetime.datetime(2016, 1, 8, 12, 0)),
 Row(a=9, b=5.0, c='string3', d=datetime.date(2000, 3, 1), e=datetime.datetime(2019, 1, 9, 12, 0)),
 Row(a=10, b=5.0, c='string3', d=datetime.date(2000, 3, 1), e=datetime.datetime(2018, 1, 10, 12, 0)),
 Row(a=11, b=5.0, c='string3', d=datetime.date(2000, 3, 1), e=datetime.datetime(2021, 1, 12, 12, 0))]

In [0]:
df.take(3)

Out[13]: [Row(a=1, b=2.0, c='string1', d=datetime.date(2000, 1, 1), e=datetime.datetime(2000, 1, 1, 12, 0)),
 Row(a=2, b=3.0, c='string2', d=datetime.date(2000, 2, 1), e=datetime.datetime(2000, 1, 2, 12, 0)),
 Row(a=4, b=5.0, c='string3', d=datetime.date(2000, 3, 1), e=datetime.datetime(2000, 1, 3, 12, 0))]

In [0]:
df.tail(1)

Out[14]: [Row(a=11, b=5.0, c='string3', d=datetime.date(2000, 3, 1), e=datetime.datetime(2021, 1, 12, 12, 0))]

***Pro Tip***

A maioria das funções em spark seguem a estrutura Camel case. >> camelCase

https://en.wikipedia.org/wiki/Camel_case

## Ingestão de dados

##### Spark e Pandas

Existe a possibilidade de fazer ingestão de dados desde várias fontes de dados. uma destas possibilidades é através dum pandas dataframe

In [0]:
df = pd.DataFrame(np.random.randint(0,100,size=(100, 4)), columns=list('ABCD'))

In [0]:
df

A 
 B 
 C 
 D 
 
 
 
 
 0 
 85 
 70 
 90 
 24 
 
 
 1 
 46 
 54 
 74 
 58 
 
 
 2 
 51 
 20 
 88 
 32 
 
 
 3 
 29 
 53 
 11 
 81 
 
 
 4 
 5 
 85 
 59 
 5 
 
 
 ... 
 ... 
 ... 
 ... 
 ... 
 
 
 95 
 82 
 44 
 79 
 98 
 
 
 96 
 32 
 30 
 22 
 65 
 
 
 97 
 34 
 80 
 6 
 71 
 
 
 98 
 90 
 74 
 22 
 3 
 
 
 99 
 58 
 95 
 34 
 84 
 
 
 
 100 rows × 4 columns

Transformando o Pandas df para um SparkDf

In [0]:
spdf = spark.createDataFrame(df)

In [0]:
spdf.show(5)

spdf.printSchema()

+---+---+---+---+
|  A|  B|  C|  D|
+---+---+---+---+
| 85| 70| 90| 24|
| 46| 54| 74| 58|
| 51| 20| 88| 32|
| 29| 53| 11| 81|
|  5| 85| 59|  5|
+---+---+---+---+
only showing top 5 rows

root
 |-- A: long (nullable = true)
 |-- B: long (nullable = true)
 |-- C: long (nullable = true)
 |-- D: long (nullable = true)



Se por alguma razão for necessário usar `"python"` ou uma *API (library)* de python não distribuída (pandas), é possível passar um spark Dataframe a um pandas dataframe. Convem ter presente  as limitações do pandas e perceber que esta solução não seja óptima em datasets muito grandes:
 

* Perder-se-á as capacidade de computação e de armazenamento distriuído
* Perder-se-á a capaciadade de lazy computation tudo será computado mal seja dada a instrução
* Perder-se-á a capacidade de processamento out-of-core e spill to disk
* Criar-se-a um *bottle neck* porque todo o dataframe terád e ser armazenado em RAM. o que faz que no caso de falta de RAM não se completará a operação

In [0]:
spdf.toPandas()

Out[19]:

A 
 B 
 C 
 D 
 
 
 
 
 0 
 50 
 46 
 3 
 89 
 
 
 1 
 67 
 52 
 38 
 86 
 
 
 2 
 32 
 63 
 21 
 65 
 
 
 3 
 36 
 98 
 64 
 62 
 
 
 4 
 74 
 73 
 13 
 38 
 
 
 ... 
 ... 
 ... 
 ... 
 ... 
 
 
 95 
 92 
 73 
 46 
 96 
 
 
 96 
 86 
 58 
 77 
 80 
 
 
 97 
 12 
 10 
 23 
 84 
 
 
 98 
 63 
 37 
 82 
 55 
 
 
 99 
 59 
 8 
 34 
 21 
 
 
 
 100 rows × 4 columns

#### CSV

In [0]:
# File location and type
file_location = "/FileStore/tables/patient_admission_dataset.csv"
file_type = "csv"

# CSV options
infer_schema = "true"
first_row_is_header = "true"
delimiter = ","

# The applied options are for CSV files. For other file types, these will be ignored.
df = spark.read.format(file_type) \
  .option("inferSchema", infer_schema) \
  .option("header", True) \
  .option("sep", delimiter) \
  .load(file_location)

display(df)

id patient_name patient_email doctor_phone patient_gender patient_dob patient_diabetic patient_allergic patient_weight_kg patient_height_sm patient_nhs_number doctor_name appointment_date patient_show is_regular_visit prescribed_medicines diagnosis 1 Celestyna Dillimore cdillimore0@dion.ne.jp 674-914-1212 Female 2018-10-18 false true 59 176 8200151867 Sarena Waliszek 2018-05-01 true true triamcinolone acetonide I669 2 Meta Michieli mmichieli1@loc.gov 172-580-3586 Female 2018-02-08 false true 77 186 null Farris Robinet 2017-12-07 true true null null 3 Cordie Sancto csancto2@cafepress.com 794-222-5085 Female 2018-10-09 true true 90 177 6145594128 Kaspar Spitaro 2018-10-05 false false null null 4 Josh De Ambrosis jde3@amazon.co.jp 856-540-5195 Male 2018-09-10 true true 70 150 null Rafferty Fowls 2018-10-21 false true null null 5 Delinda Alfonsini dalfonsini4@opensource.org 938-978-1131 Female 2018-02-26 false true 82 140 480475776 Glenna MacNeachtain 2018-11-15 false false null null 6 Sharlene Gladwell sgladwell5@ca.gov 189-606-8362 Female 2018-08-15 false true 105 179 7051325396 Cissy Markey 2018-11-12 false true null null 7 Bronny Muldoon bmuldoon6@freewebs.com 918-980-6452 Male 2018-07-17 true true 87 180 8220808950 Cissy Markey 2018-02-21 false false octinoxate, avobenzone, and octocrylene S72309N 8 Shalne Fierman sfierman7@surveymonkey.com 751-108-0933 Female 2018-02-08 false false 73 152 null Ryley Swallow 2018-02-02 false false null null 9 Booth Dumphy bdumphy8@hao123.com 763-503-3391 Male 2018-10-05 true false 83 156 3999567651 Sarena Waliszek 2018-01-01 false false Glipizide and Metformin Hydrochloride T508X6 10 Wallas Delacourt wdelacourt9@google.com.hk 711-619-5682 Male 2017-12-29 false false 89 160 2200400896 Wyn Grassett 2018-08-08 true false null null 11 Luca Carthew lcarthewa@tuttocitta.it 870-310-2489 Male 2018-08-30 true true 108 165 6065749575 Dulce McKerley 2018-01-28 false true Benazepril Hydrochloride S420 12 Peg Cosgry pcosgryb@nsw.gov.au 437-655-8584 Female 2018-07-18 false false 53 147 null Ryley Swallow 2018-01-21 false true WITCH HAZEL T8743 13 Hugo Pllu hplluc@ox.ac.uk 726-348-8191 Male 2018-04-09 true false 51 170 2421595800 Cissy Markey 2018-10-31 true true Terbinafine Hydrochloride M80072A 14 Hogan Turl hturld@tmall.com 754-361-7871 Male 2018-10-03 true true 106 142 null Dulce McKerley 2018-08-24 true false null null 15 Therine Ivers tiverse@webeden.co.uk 894-719-4146 Female 2018-05-29 false true 58 169 1286894182 Gabie Brafield 2017-12-18 false false null null 16 Normy Tuckie ntuckief@uiuc.edu 295-405-7288 Male 2017-11-30 true false 64 150 8229454531 Oralie Swaffer 2018-08-30 false false null null 17 Mella Jermey mjermeyg@mozilla.com 819-883-4582 Female 2017-11-24 true false 56 168 454921179 Wyn Grassett 2018-01-22 true true Tretinoin T22342A 18 Meridel Oldfield-Cherry moldfieldcherryh@slideshare.net 196-753-2182 Female 2018-06-07 false true 69 182 4747845429 Humfried Cartmel 2018-03-06 true false null null 19 Rowen Flanagan rflanagani@ed.gov 378-633-7181 Male 2018-10-31 false true 69 178 5933292168 Madelina Scurrell 2018-11-02 false true null null 20 Stormie Weildish sweildishj@github.io 376-854-4953 Female 2018-01-09 false true 77 155 3929474875 Farris Robinet 2018-05-15 true true null null 21 Granny Conford gconfordk@about.me 106-374-5769 Male 2018-05-20 true false 89 153 null Ryley Swallow 2018-10-10 false true Magesium Citrate S06378S 22 Winifield Tappor wtapporl@illinois.edu 461-360-7673 Male 2018-09-05 true false 70 153 null Sarena Waliszek 2018-04-21 true true null null 23 Anny Eburah aeburahm@ovh.net 995-335-6068 Female 2018-02-17 true true 102 182 7808845663 Wyn Grassett 2018-08-26 true false Psyllium Husks T23269 24 Edmon Dealey edealeyn@tinyurl.com 179-617-0069 Male 2017-12-24 false false 52 152 null Sarena Waliszek 2018-09-09 true false aluminum hydroxide Y37251D 25 Maximilianus Brendish mbrendisho@msu.edu 629-415-9519 Male 2018-06-25 true true 75 181 8172235763 Ryley Swallow 2018-03-12

In [0]:
df.printSchema()

root
 |-- id: integer (nullable = true)
 |-- patient_name: string (nullable = true)
 |-- patient_email: string (nullable = true)
 |-- doctor_phone: string (nullable = true)
 |-- patient_gender: string (nullable = true)
 |-- patient_dob: date (nullable = true)
 |-- patient_diabetic: boolean (nullable = true)
 |-- patient_allergic: boolean (nullable = true)
 |-- patient_weight_kg: integer (nullable = true)
 |-- patient_height_sm: integer (nullable = true)
 |-- patient_nhs_number: long (nullable = true)
 |-- doctor_name: string (nullable = true)
 |-- appointment_date: date (nullable = true)
 |-- patient_show: boolean (nullable = true)
 |-- is_regular_visit: boolean (nullable = true)
 |-- prescribed_medicines: string (nullable = true)
 |-- diagnosis: string (nullable = true)



Ao ler o CSV e não é definido previamente o schema e o `infer_schema = False`  faz que todas as columnas são assumidas como string . Ora façamos o mesmo com o `infer_schema = True`

In [0]:
# The applied options are for CSV files. For other file types, these will be ignored.
df = spark.read.format(file_type) \
  .option("inferSchema", True) \
  .option("header", True) \
  .option("sep", delimiter) \
  .load(file_location)

display(df)

id patient_name patient_email doctor_phone patient_gender patient_dob patient_diabetic patient_allergic patient_weight_kg patient_height_sm patient_nhs_number doctor_name appointment_date patient_show is_regular_visit prescribed_medicines diagnosis 1 Celestyna Dillimore cdillimore0@dion.ne.jp 674-914-1212 Female 2018-10-18 false true 59 176 8200151867 Sarena Waliszek 2018-05-01 true true triamcinolone acetonide I669 2 Meta Michieli mmichieli1@loc.gov 172-580-3586 Female 2018-02-08 false true 77 186 null Farris Robinet 2017-12-07 true true null null 3 Cordie Sancto csancto2@cafepress.com 794-222-5085 Female 2018-10-09 true true 90 177 6145594128 Kaspar Spitaro 2018-10-05 false false null null 4 Josh De Ambrosis jde3@amazon.co.jp 856-540-5195 Male 2018-09-10 true true 70 150 null Rafferty Fowls 2018-10-21 false true null null 5 Delinda Alfonsini dalfonsini4@opensource.org 938-978-1131 Female 2018-02-26 false true 82 140 480475776 Glenna MacNeachtain 2018-11-15 false false null null 6 Sharlene Gladwell sgladwell5@ca.gov 189-606-8362 Female 2018-08-15 false true 105 179 7051325396 Cissy Markey 2018-11-12 false true null null 7 Bronny Muldoon bmuldoon6@freewebs.com 918-980-6452 Male 2018-07-17 true true 87 180 8220808950 Cissy Markey 2018-02-21 false false octinoxate, avobenzone, and octocrylene S72309N 8 Shalne Fierman sfierman7@surveymonkey.com 751-108-0933 Female 2018-02-08 false false 73 152 null Ryley Swallow 2018-02-02 false false null null 9 Booth Dumphy bdumphy8@hao123.com 763-503-3391 Male 2018-10-05 true false 83 156 3999567651 Sarena Waliszek 2018-01-01 false false Glipizide and Metformin Hydrochloride T508X6 10 Wallas Delacourt wdelacourt9@google.com.hk 711-619-5682 Male 2017-12-29 false false 89 160 2200400896 Wyn Grassett 2018-08-08 true false null null 11 Luca Carthew lcarthewa@tuttocitta.it 870-310-2489 Male 2018-08-30 true true 108 165 6065749575 Dulce McKerley 2018-01-28 false true Benazepril Hydrochloride S420 12 Peg Cosgry pcosgryb@nsw.gov.au 437-655-8584 Female 2018-07-18 false false 53 147 null Ryley Swallow 2018-01-21 false true WITCH HAZEL T8743 13 Hugo Pllu hplluc@ox.ac.uk 726-348-8191 Male 2018-04-09 true false 51 170 2421595800 Cissy Markey 2018-10-31 true true Terbinafine Hydrochloride M80072A 14 Hogan Turl hturld@tmall.com 754-361-7871 Male 2018-10-03 true true 106 142 null Dulce McKerley 2018-08-24 true false null null 15 Therine Ivers tiverse@webeden.co.uk 894-719-4146 Female 2018-05-29 false true 58 169 1286894182 Gabie Brafield 2017-12-18 false false null null 16 Normy Tuckie ntuckief@uiuc.edu 295-405-7288 Male 2017-11-30 true false 64 150 8229454531 Oralie Swaffer 2018-08-30 false false null null 17 Mella Jermey mjermeyg@mozilla.com 819-883-4582 Female 2017-11-24 true false 56 168 454921179 Wyn Grassett 2018-01-22 true true Tretinoin T22342A 18 Meridel Oldfield-Cherry moldfieldcherryh@slideshare.net 196-753-2182 Female 2018-06-07 false true 69 182 4747845429 Humfried Cartmel 2018-03-06 true false null null 19 Rowen Flanagan rflanagani@ed.gov 378-633-7181 Male 2018-10-31 false true 69 178 5933292168 Madelina Scurrell 2018-11-02 false true null null 20 Stormie Weildish sweildishj@github.io 376-854-4953 Female 2018-01-09 false true 77 155 3929474875 Farris Robinet 2018-05-15 true true null null 21 Granny Conford gconfordk@about.me 106-374-5769 Male 2018-05-20 true false 89 153 null Ryley Swallow 2018-10-10 false true Magesium Citrate S06378S 22 Winifield Tappor wtapporl@illinois.edu 461-360-7673 Male 2018-09-05 true false 70 153 null Sarena Waliszek 2018-04-21 true true null null 23 Anny Eburah aeburahm@ovh.net 995-335-6068 Female 2018-02-17 true true 102 182 7808845663 Wyn Grassett 2018-08-26 true false Psyllium Husks T23269 24 Edmon Dealey edealeyn@tinyurl.com 179-617-0069 Male 2017-12-24 false false 52 152 null Sarena Waliszek 2018-09-09 true false aluminum hydroxide Y37251D 25 Maximilianus Brendish mbrendisho@msu.edu 629-415-9519 Male 2018-06-25 true true 75 181 8172235763 Ryley Swallow 2018-03-12

In [0]:
df.printSchema()

root
 |-- id: integer (nullable = true)
 |-- patient_name: string (nullable = true)
 |-- patient_email: string (nullable = true)
 |-- doctor_phone: string (nullable = true)
 |-- patient_gender: string (nullable = true)
 |-- patient_dob: date (nullable = true)
 |-- patient_diabetic: boolean (nullable = true)
 |-- patient_allergic: boolean (nullable = true)
 |-- patient_weight_kg: integer (nullable = true)
 |-- patient_height_sm: integer (nullable = true)
 |-- patient_nhs_number: long (nullable = true)
 |-- doctor_name: string (nullable = true)
 |-- appointment_date: date (nullable = true)
 |-- patient_show: boolean (nullable = true)
 |-- is_regular_visit: boolean (nullable = true)
 |-- prescribed_medicines: string (nullable = true)
 |-- diagnosis: string (nullable = true)



Não necessáriamente o `infer_schema` consegue detectar corretamente os datatypes que se pretendem, . podemos *forçar*  e determinar o schema e os datatypes antes da importação, ficamos com a certeza de que os datatypes estão certos, e que não vamos ter error no processamento futuro

In [0]:
from pyspark.sql.types import *
schema = StructType([
StructField("id",IntegerType()),
StructField("patient_name",StringType()),
StructField("patient_email",StringType()),
StructField("doctor_phone",StringType()),
StructField("patient_gender",StringType()),
StructField("patient_dob",DateType()),
StructField("patient_diabetic",BooleanType()),
StructField("patient_allergic",BooleanType()),
StructField("patient_weight_kg",IntegerType()),
StructField("patient_height_sm",IntegerType()),
StructField("patient_nhs_number",LongType()),
StructField("doctor_name",StringType()),
StructField("appointment_date",DateType()),
StructField("patient_show",BooleanType()),
StructField("is_regular_visit",BooleanType()),
StructField("prescribed_medicines",StringType()),
StructField("diagnosis",StringType())
])

file_type ='csv'
delimiter = ','
#file_location = "/FileStore/tables/patient_admission_dataset_for_learning_data_mining-1.csv"


In [0]:
df = spark.read.format(file_type) \
  .option("header", True) \
  .option("sep", delimiter) \
  .schema(schema)\
  .load(file_location)


In [0]:
df.printSchema()

root
 |-- id: integer (nullable = true)
 |-- patient_name: string (nullable = true)
 |-- patient_email: string (nullable = true)
 |-- doctor_phone: string (nullable = true)
 |-- patient_gender: string (nullable = true)
 |-- patient_dob: date (nullable = true)
 |-- patient_diabetic: boolean (nullable = true)
 |-- patient_allergic: boolean (nullable = true)
 |-- patient_weight_kg: integer (nullable = true)
 |-- patient_height_sm: integer (nullable = true)
 |-- patient_nhs_number: long (nullable = true)
 |-- doctor_name: string (nullable = true)
 |-- appointment_date: date (nullable = true)
 |-- patient_show: boolean (nullable = true)
 |-- is_regular_visit: boolean (nullable = true)
 |-- prescribed_medicines: string (nullable = true)
 |-- diagnosis: string (nullable = true)



In [0]:
df.display()

id patient_name patient_email doctor_phone patient_gender patient_dob patient_diabetic patient_allergic patient_weight_kg patient_height_sm patient_nhs_number doctor_name appointment_date patient_show is_regular_visit prescribed_medicines diagnosis 1 Celestyna Dillimore cdillimore0@dion.ne.jp 674-914-1212 Female null false true 59 176 8200151867 Sarena Waliszek null true true triamcinolone acetonide I669 2 Meta Michieli mmichieli1@loc.gov 172-580-3586 Female null false true 77 186 null Farris Robinet null true true null null 3 Cordie Sancto csancto2@cafepress.com 794-222-5085 Female null true true 90 177 6145594128 Kaspar Spitaro null false false null null 4 Josh De Ambrosis jde3@amazon.co.jp 856-540-5195 Male null true true 70 150 null Rafferty Fowls null false true null null 5 Delinda Alfonsini dalfonsini4@opensource.org 938-978-1131 Female null false true 82 140 480475776 Glenna MacNeachtain null false false null null 6 Sharlene Gladwell sgladwell5@ca.gov 189-606-8362 Female null false true 105 179 7051325396 Cissy Markey null false true null null 7 Bronny Muldoon bmuldoon6@freewebs.com 918-980-6452 Male null true true 87 180 8220808950 Cissy Markey null false false octinoxate, avobenzone, and octocrylene S72309N 8 Shalne Fierman sfierman7@surveymonkey.com 751-108-0933 Female null false false 73 152 null Ryley Swallow null false false null null 9 Booth Dumphy bdumphy8@hao123.com 763-503-3391 Male null true false 83 156 3999567651 Sarena Waliszek null false false Glipizide and Metformin Hydrochloride T508X6 10 Wallas Delacourt wdelacourt9@google.com.hk 711-619-5682 Male null false false 89 160 2200400896 Wyn Grassett null true false null null 11 Luca Carthew lcarthewa@tuttocitta.it 870-310-2489 Male null true true 108 165 6065749575 Dulce McKerley null false true Benazepril Hydrochloride S420 12 Peg Cosgry pcosgryb@nsw.gov.au 437-655-8584 Female null false false 53 147 null Ryley Swallow null false true WITCH HAZEL T8743 13 Hugo Pllu hplluc@ox.ac.uk 726-348-8191 Male null true false 51 170 2421595800 Cissy Markey null true true Terbinafine Hydrochloride M80072A 14 Hogan Turl hturld@tmall.com 754-361-7871 Male null true true 106 142 null Dulce McKerley null true false null null 15 Therine Ivers tiverse@webeden.co.uk 894-719-4146 Female null false true 58 169 1286894182 Gabie Brafield null false false null null 16 Normy Tuckie ntuckief@uiuc.edu 295-405-7288 Male null true false 64 150 8229454531 Oralie Swaffer null false false null null 17 Mella Jermey mjermeyg@mozilla.com 819-883-4582 Female null true false 56 168 454921179 Wyn Grassett null true true Tretinoin T22342A 18 Meridel Oldfield-Cherry moldfieldcherryh@slideshare.net 196-753-2182 Female null false true 69 182 4747845429 Humfried Cartmel null true false null null 19 Rowen Flanagan rflanagani@ed.gov 378-633-7181 Male null false true 69 178 5933292168 Madelina Scurrell null false true null null 20 Stormie Weildish sweildishj@github.io 376-854-4953 Female null false true 77 155 3929474875 Farris Robinet null true true null null 21 Granny Conford gconfordk@about.me 106-374-5769 Male null true false 89 153 null Ryley Swallow null false true Magesium Citrate S06378S 22 Winifield Tappor wtapporl@illinois.edu 461-360-7673 Male null true false 70 153 null Sarena Waliszek null true true null null 23 Anny Eburah aeburahm@ovh.net 995-335-6068 Female null true true 102 182 7808845663 Wyn Grassett null true false Psyllium Husks T23269 24 Edmon Dealey edealeyn@tinyurl.com 179-617-0069 Male null false false 52 152 null Sarena Waliszek null true false aluminum hydroxide Y37251D 25 Maximilianus Brendish mbrendisho@msu.edu 629-415-9519 Male null true true 75 181 8172235763 Ryley Swallow null false false Estradiol S42491G 26 Selie Duff sduffp@behance.net 695-648-5659 Female null false false 98 177 9490815780 Glenna MacNeachtain null false false null null 27 Virgie Veillard vveillardq@mit.edu 956-594-1648 Female null false true 62 171 4151113673 Madelina Scurrell null true true null null

## Selecionar dados

In [0]:
pdf = df.toPandas()

#### 1. Selecionar uma coluna num  <span style="color:DarkBlue">***DataFrame***</span>

* Pandas

In [0]:
pdf[['id']]

id 
 
 
 
 
 0 
 1 
 
 
 1 
 2 
 
 
 2 
 3 
 
 
 3 
 4 
 
 
 4 
 5 
 
 
 ... 
 ... 
 
 
 995 
 996 
 
 
 996 
 997 
 
 
 997 
 998 
 
 
 998 
 999 
 
 
 999 
 1000 
 
 
 
 1000 rows × 1 columns

* Pyspark

In [0]:
#muito parecido como é feito em SQL
df.select('id').show(2)

+---+
| id|
+---+
|  1|
|  2|
+---+
only showing top 2 rows



#### selecionar mais de 1 variável
seleccione id, doctor_phone e patient_email

In [0]:
pdf[['doctor_phone','appointment_date']]

doctor_phone 
 appointment_date 
 
 
 
 
 0 
 674-914-1212 
 None 
 
 
 1 
 172-580-3586 
 None 
 
 
 2 
 794-222-5085 
 None 
 
 
 3 
 856-540-5195 
 None 
 
 
 4 
 938-978-1131 
 None 
 
 
 ... 
 ... 
 ... 
 
 
 995 
 131-633-7402 
 None 
 
 
 996 
 628-914-7040 
 None 
 
 
 997 
 507-286-3685 
 None 
 
 
 998 
 921-567-6180 
 None 
 
 
 999 
 493-288-3036 
 None 
 
 
 
 1000 rows × 2 columns

In [0]:
# existem 3 formas de seleccionar ou "chamar" as colunas em pyspark
# cá veremos 2 formas

df.select(df.doctor_phone, df.appointment_date, 'id').show(5)

+------------+----------------+---+
|doctor_phone|appointment_date| id|
+------------+----------------+---+
|674-914-1212|            null|  1|
|172-580-3586|            null|  2|
|794-222-5085|            null|  3|
|856-540-5195|            null|  4|
|938-978-1131|            null|  5|
+------------+----------------+---+
only showing top 5 rows



Ver todas as colunas dentro de um dataframe

In [0]:
# exatamente como é feito em pandas
df.columns

Out[40]: ['id',
 'patient_name',
 'patient_email',
 'doctor_phone',
 'patient_gender',
 'patient_dob',
 'patient_diabetic',
 'patient_allergic',
 'patient_weight_kg',
 'patient_height_sm',
 'patient_nhs_number',
 'doctor_name',
 'appointment_date',
 'patient_show',
 'is_regular_visit',
 'prescribed_medicines',
 'diagnosis']

#### 2. Criar uma nova coluna calculada, ou seja uma coluna nova baseada numa outra existente no  <span style="color:DarkBlue">**DataFrame**</span> existente.
Passar os nomes dos doentes a Uppercase

* Pandas

In [0]:
pdf['whatever'] = pdf['patient_name'].str.upper()

In [0]:
pdf[['whatever']]

whatever 
 
 
 
 
 0 
 CELESTYNA DILLIMORE 
 
 
 1 
 META MICHIELI 
 
 
 2 
 CORDIE SANCTO 
 
 
 3 
 JOSH DE AMBROSIS 
 
 
 4 
 DELINDA ALFONSINI 
 
 
 ... 
 ... 
 
 
 995 
 GERMAIN NINNOTTI 
 
 
 996 
 TARA PLEWRIGHT 
 
 
 997 
 SELIG CREYKE 
 
 
 998 
 MANNY TRENAMAN 
 
 
 999 
 CRISTOBAL FIELLER 
 
 
 
 1000 rows × 1 columns

* Pyspark

* Diferentes formas de selecionar uma coluna no spark dataframe

In [0]:
# cá temos as 3 formas de seleccionar as colunas
# 1. "coluna"
# 2. dataframe.coluna
# 3. col.coluna tem de se importar a função ´col´

from pyspark.sql.functions import col
df.select("patient_name", df.patient_name, df["patient_name"], col("patient_name")).show()

---------------------------------------------------------------------------
ModuleNotFoundError                       Traceback (most recent call last)
c:\Users\gadim\Desktop\EDIT\20231\BDA\Spark\lab\2.Intro Pyspark.ipynb Cell 74 in <cell line: 6>()
      <a href='vscode-notebook-cell:/c%3A/Users/gadim/Desktop/EDIT/20231/BDA/Spark/lab/2.Intro%20Pyspark.ipynb#Y133sZmlsZQ%3D%3D?line=0'>1</a> # cá temos as 3 formas de seleccionar as colunas
      <a href='vscode-notebook-cell:/c%3A/Users/gadim/Desktop/EDIT/20231/BDA/Spark/lab/2.Intro%20Pyspark.ipynb#Y133sZmlsZQ%3D%3D?line=1'>2</a> # 1. "coluna"
      <a href='vscode-notebook-cell:/c%3A/Users/gadim/Desktop/EDIT/20231/BDA/Spark/lab/2.Intro%20Pyspark.ipynb#Y133sZmlsZQ%3D%3D?line=2'>3</a> # 2. dataframe.coluna
      <a href='vscode-notebook-cell:/c%3A/Users/gadim/Desktop/EDIT/20231/BDA/Spark/lab/2.Intro%20Pyspark.ipynb#Y133sZmlsZQ%3D%3D?line=3'>4</a> # 3. col.coluna tem de se importar a função ´col´
----> <a href='vscode-notebook-cell:/c%3A/U

**WithColum**: 
  
para <span style="color:orange">**CRIAR**</span> ou <span style="color:red">**SUBSTITUIR**</span> uma coluna em pyspark é usado `dataFrame.withColumn()`. É uma função que afeta diretamente o dataframe, por conseguinte retorna um dataframe

https://spark.apache.org/docs/latest/api/python/reference/api/pyspark.sql.DataFrame.withColumn.html
  
 Outras Funções:
 
* Vamos usar a função `upper` que permite transformar quaisquer strings em uppercase: https://spark.apache.org/docs/latest/api/python/reference/api/pyspark.sql.functions.upper.html#pyspark.sql.functions.upper
* Função `col` que permite a chamar a coluna do dataframe que esta a ser afetado pelo o seu nome: 
https://spark.apache.org/docs/latest/api/python/reference/api/pyspark.sql.functions.col.html#pyspark.sql.functions.col

In [0]:
from pyspark.sql.functions import upper
from pyspark.sql.functions import col

In [0]:
df = df.withColumn('Cap_name',upper(df.patient_name)) 

In [0]:
df.select("Cap_name")

Out[45]: DataFrame[Cap_name: string]

In [0]:
df.display()

id patient_name patient_email doctor_phone patient_gender patient_dob patient_diabetic patient_allergic patient_weight_kg patient_height_sm patient_nhs_number doctor_name appointment_date patient_show is_regular_visit prescribed_medicines diagnosis Cap_name 1 Celestyna Dillimore cdillimore0@dion.ne.jp 674-914-1212 Female null false true 59 176 8200151867 Sarena Waliszek null true true triamcinolone acetonide I669 CELESTYNA DILLIMORE 2 Meta Michieli mmichieli1@loc.gov 172-580-3586 Female null false true 77 186 null Farris Robinet null true true null null META MICHIELI 3 Cordie Sancto csancto2@cafepress.com 794-222-5085 Female null true true 90 177 6145594128 Kaspar Spitaro null false false null null CORDIE SANCTO 4 Josh De Ambrosis jde3@amazon.co.jp 856-540-5195 Male null true true 70 150 null Rafferty Fowls null false true null null JOSH DE AMBROSIS 5 Delinda Alfonsini dalfonsini4@opensource.org 938-978-1131 Female null false true 82 140 480475776 Glenna MacNeachtain null false false null null DELINDA ALFONSINI 6 Sharlene Gladwell sgladwell5@ca.gov 189-606-8362 Female null false true 105 179 7051325396 Cissy Markey null false true null null SHARLENE GLADWELL 7 Bronny Muldoon bmuldoon6@freewebs.com 918-980-6452 Male null true true 87 180 8220808950 Cissy Markey null false false octinoxate, avobenzone, and octocrylene S72309N BRONNY MULDOON 8 Shalne Fierman sfierman7@surveymonkey.com 751-108-0933 Female null false false 73 152 null Ryley Swallow null false false null null SHALNE FIERMAN 9 Booth Dumphy bdumphy8@hao123.com 763-503-3391 Male null true false 83 156 3999567651 Sarena Waliszek null false false Glipizide and Metformin Hydrochloride T508X6 BOOTH DUMPHY 10 Wallas Delacourt wdelacourt9@google.com.hk 711-619-5682 Male null false false 89 160 2200400896 Wyn Grassett null true false null null WALLAS DELACOURT 11 Luca Carthew lcarthewa@tuttocitta.it 870-310-2489 Male null true true 108 165 6065749575 Dulce McKerley null false true Benazepril Hydrochloride S420 LUCA CARTHEW 12 Peg Cosgry pcosgryb@nsw.gov.au 437-655-8584 Female null false false 53 147 null Ryley Swallow null false true WITCH HAZEL T8743 PEG COSGRY 13 Hugo Pllu hplluc@ox.ac.uk 726-348-8191 Male null true false 51 170 2421595800 Cissy Markey null true true Terbinafine Hydrochloride M80072A HUGO PLLU 14 Hogan Turl hturld@tmall.com 754-361-7871 Male null true true 106 142 null Dulce McKerley null true false null null HOGAN TURL 15 Therine Ivers tiverse@webeden.co.uk 894-719-4146 Female null false true 58 169 1286894182 Gabie Brafield null false false null null THERINE IVERS 16 Normy Tuckie ntuckief@uiuc.edu 295-405-7288 Male null true false 64 150 8229454531 Oralie Swaffer null false false null null NORMY TUCKIE 17 Mella Jermey mjermeyg@mozilla.com 819-883-4582 Female null true false 56 168 454921179 Wyn Grassett null true true Tretinoin T22342A MELLA JERMEY 18 Meridel Oldfield-Cherry moldfieldcherryh@slideshare.net 196-753-2182 Female null false true 69 182 4747845429 Humfried Cartmel null true false null null MERIDEL OLDFIELD-CHERRY 19 Rowen Flanagan rflanagani@ed.gov 378-633-7181 Male null false true 69 178 5933292168 Madelina Scurrell null false true null null ROWEN FLANAGAN 20 Stormie Weildish sweildishj@github.io 376-854-4953 Female null false true 77 155 3929474875 Farris Robinet null true true null null STORMIE WEILDISH 21 Granny Conford gconfordk@about.me 106-374-5769 Male null true false 89 153 null Ryley Swallow null false true Magesium Citrate S06378S GRANNY CONFORD 22 Winifield Tappor wtapporl@illinois.edu 461-360-7673 Male null true false 70 153 null Sarena Waliszek null true true null null WINIFIELD TAPPOR 23 Anny Eburah aeburahm@ovh.net 995-335-6068 Female null true true 102 182 7808845663 Wyn Grassett null true false Psyllium Husks T23269 ANNY EBURAH 24 Edmon Dealey edealeyn@tinyurl.com 179-617-0069 Male null false false 52 152 null Sarena Waliszek null true false aluminum hydroxide Y37251D EDMON DEALEY 25 Maximilianus Brendish mbrendisho@msu.edu 6

In [0]:
df.select('Cap_name').show()

+--------------------+
|            Cap_name|
+--------------------+
| CELESTYNA DILLIMORE|
|       META MICHIELI|
|       CORDIE SANCTO|
|    JOSH DE AMBROSIS|
|   DELINDA ALFONSINI|
|   SHARLENE GLADWELL|
|      BRONNY MULDOON|
|      SHALNE FIERMAN|
|        BOOTH DUMPHY|
|    WALLAS DELACOURT|
|        LUCA CARTHEW|
|          PEG COSGRY|
|           HUGO PLLU|
|          HOGAN TURL|
|       THERINE IVERS|
|        NORMY TUCKIE|
|        MELLA JERMEY|
|MERIDEL OLDFIELD-...|
|      ROWEN FLANAGAN|
|    STORMIE WEILDISH|
+--------------------+
only showing top 20 rows



#### 3. Criar uma  nova <span style="color:DarkBlue">***coluna***</span> com único valor

In [0]:
pdf['sc'] = 1

* Pandas

In [0]:
pdf[['sc']]

sc 
 
 
 
 
 0 
 1 
 
 
 1 
 1 
 
 
 2 
 1 
 
 
 3 
 1 
 
 
 4 
 1 
 
 
 ... 
 ... 
 
 
 995 
 1 
 
 
 996 
 1 
 
 
 997 
 1 
 
 
 998 
 1 
 
 
 999 
 1 
 
 
 
 1000 rows × 1 columns

* Pyspark

**lit**

para poder criar uma coluna com um <span style="color:DarkBlue">**unico valor**</span> que se repita no dataframe inteiro não suficiente fazer a mesma operação como é feita no pandas. Temos de usar a função `lit`
https://spark.apache.org/docs/latest/api/python/reference/api/pyspark.sql.functions.lit.html#pyspark.sql.functions.lit

In [0]:
from pyspark.sql.functions import lit

In [0]:
df = df.withColumn('escalar',lit('sdgfgsdfd'))

In [0]:
df

Out[50]: DataFrame[id: int, patient_name: string, patient_email: string, doctor_phone: string, patient_gender: string, patient_dob: date, patient_diabetic: boolean, patient_allergic: boolean, patient_weight_kg: int, patient_height_sm: int, patient_nhs_number: bigint, doctor_name: string, appointment_date: date, patient_show: boolean, is_regular_visit: boolean, prescribed_medicines: string, diagnosis: string, Cap_name: string, escalar: string]

In [0]:
df.select('escalar').show(3)

+---------+
|  escalar|
+---------+
|sdgfgsdfd|
|sdgfgsdfd|
|sdgfgsdfd|
+---------+
only showing top 3 rows



#### 4. Filtrar <span style="color:DarkBlue">***DataFrames***</span> segundo condições

* Pandas

In [0]:
pdf[pdf['whatever'] == 'META MICHIELI']

id 
 patient_name 
 patient_email 
 doctor_phone 
 patient_gender 
 patient_dob 
 patient_diabetic 
 patient_allergic 
 patient_weight_kg 
 patient_height_sm 
 patient_nhs_number 
 doctor_name 
 appointment_date 
 patient_show 
 is_regular_visit 
 prescribed_medicines 
 diagnosis 
 whatever 
 
 
 
 
 1 
 2 
 Meta Michieli 
 mmichieli1@loc.gov 
 172-580-3586 
 Female 
 None 
 False 
 True 
 77 
 186 
 NaN 
 Farris Robinet 
 None 
 True 
 True 
 None 
 None 
 META MICHIELI

Boolean Mask

In [0]:
pdf['whatever'] == 'META MICHIELI'

Out[53]: 0      False
1       True
2      False
3      False
4      False
       ...  
995    False
996    False
997    False
998    False
999    False
Name: whatever, Length: 1000, dtype: bool

**.Where()**

para poder filtrar é usado a função `where` ou `filter` da API dos dataframes no pyspark. Portanto, a utilização do where retorna um dataframe **não uma coluna**. O dataframe resutalte terá a mesmas colunas mas com os dados filtrados.

Pode ser usado `where` ou `filter` indistantamente. `where()` e um alias para o `filter()`

* https://spark.apache.org/docs/latest/api/python/reference/api/pyspark.sql.DataFrame.filter.html#pyspark.sql.DataFrame.filter
* https://spark.apache.org/docs/latest/api/python/reference/api/pyspark.sql.DataFrame.where.html#pyspark.sql.DataFrame.where

In [0]:
df.where(df.Cap_name == 'META MICHIELI').select("Cap_name").show()

+-------------+
|     Cap_name|
+-------------+
|META MICHIELI|
+-------------+



#### 5. Criar  <span style="color:DarkBlue">***Colunas***</span> segundo condições logicas baseadas em outras colunas.

* Pandas

**when()**

***função*** que permite avaliar condições presentes nas colunas e devolve uma de muitas expressões possíveis.

https://spark.apache.org/docs/latest/api/python/reference/pyspark.sql/api/pyspark.sql.Column.when.html

**otherwise()**

Função da API de colunas. Permite Passar um valor único a todas as possíveis condições e expressões que não foram contempladas na função `when()`

In [0]:
# GCP: 
# uma prática é importar todas as funções de pyspark e não individualmente.
import pyspark.sql.functions as F

 ***Explicit line joining***

Two or more physical lines may be joined into logical lines using backslash characters (\\), as follows: when a physical line ends in a backslash that is not part of a string literal or comment, it is joined with the following forming a single logical line, deleting the backslash and the following end-of-line character. For example:

https://docs.python.org/3/reference/lexical_analysis.html#line-structure

In [0]:
df.withColumn(
    'parsed_phone',   
    F.when(df['doctor_phone']==None, '00000-0000000')\
    .otherwise(F.lit('0sdsds')))\
    .select('parsed_phone')\
    .show()

+------------+
|parsed_phone|
+------------+
|      0sdsds|
|      0sdsds|
|      0sdsds|
|      0sdsds|
|      0sdsds|
|      0sdsds|
|      0sdsds|
|      0sdsds|
|      0sdsds|
|      0sdsds|
|      0sdsds|
|      0sdsds|
|      0sdsds|
|      0sdsds|
|      0sdsds|
|      0sdsds|
|      0sdsds|
|      0sdsds|
|      0sdsds|
|      0sdsds|
+------------+
only showing top 20 rows



In [0]:
# NÃO FAZER ISTO!!!!!!!!!
# perde-se interpreatabilidade 
# não permite fazer fácil debugging
# NO AOS COMBOIOS.

df.withColumn('parsed_phone', F.when(df['doctor_phone']==None,'00000-0000000').otherwise(F.lit('0sdsds'))).select('parsed_phone').show()

#### 6. Calcular o Máximo   <span style="color:DarkBlue">***duma coluna***</span>.

In [0]:
pdf['id'].max()

Out[49]: 1000

**Max()**

***função*** de agregação que permite calcular o máximo num grupo específico. Pode ser como função de agregação num `groupBy()` ou para calcular o valor máximo da coluna.

https://spark.apache.org/docs/latest/api/python/reference/pyspark.sql/api/pyspark.sql.functions.max.html

**Min()**

***função*** de agregação que permite calcular o mínimo num grupo específico. Pode ser como função de agregação num `groupBy()` ou para calcular o valor mínimo da coluna.

https://spark.apache.org/docs/latest/api/python/reference/pyspark.sql/api/pyspark.sql.functions.min.html?highlight=min#

In [0]:
import this

The Zen of Python, by Tim Peters

Beautiful is better than ugly.
Explicit is better than implicit.
Simple is better than complex.
Complex is better than complicated.
Flat is better than nested.
Sparse is better than dense.
Readability counts.
Special cases aren't special enough to break the rules.
Although practicality beats purity.
Errors should never pass silently.
Unless explicitly silenced.
In the face of ambiguity, refuse the temptation to guess.
There should be one-- and preferably only one --obvious way to do it.
Although that way may not be obvious at first unless you're Dutch.
Now is better than never.
Although never is often better than *right* now.
If the implementation is hard to explain, it's a bad idea.
If the implementation is easy to explain, it may be a good idea.
Namespaces are one honking great idea -- let's do more of those!


In [0]:
df.select(F.max(df['id'])).show()

---------------------------------------------------------------------------
NameError                                 Traceback (most recent call last)
c:\Users\gadim\Desktop\EDIT\20232\Intro Pyspark.ipynb Cell 105 in <cell line: 1>()
----> <a href='vscode-notebook-cell:/c%3A/Users/gadim/Desktop/EDIT/20232/Intro%20Pyspark.ipynb#Y210sZmlsZQ%3D%3D?line=0'>1</a> df.select(F.max(df['id'])).show()

NameError: name 'df' is not defined

In [0]:
df.select(
  F.max(
    df['id']  
  )
).show()

+-------+
|max(id)|
+-------+
|   1000|
+-------+



In [0]:
df.select(F.min(df['id'])).show()

+-------+
|min(id)|
+-------+
|      1|
+-------+



#### 7. <span style="color:DarkBlue">***SQL.***</span>

**SQL**

Existe a possibilidade de  usar a linguagem SQL. existem varias formas de conseguí-lo.


1. Criar uma tabela temporário
2. Criar uma tabela 




**createOrReplaceTempView()**

Cria uma ***view local*** temporária que permite acceder com a linguagem SQL. a view local Faz recurso à Memoria RAM.

https://spark.apache.org/docs/latest/api/python/reference/pyspark.sql/api/pyspark.sql.DataFrame.createOrReplaceTempView.html


Para Poder fazer uso de SQL dentro de Pyspark é necessário usar `spark.sql()`

In [0]:
name = "testsql"
df.createOrReplaceTempView(name)

In [0]:
%sql
SELECT *
FROM testsql



id patient_name patient_email doctor_phone patient_gender patient_dob patient_diabetic patient_allergic patient_weight_kg patient_height_sm patient_nhs_number doctor_name appointment_date patient_show is_regular_visit prescribed_medicines diagnosis Cap_name escalar 1 Celestyna Dillimore cdillimore0@dion.ne.jp 674-914-1212 Female null false true 59 176 8200151867 Sarena Waliszek null true true triamcinolone acetonide I669 CELESTYNA DILLIMORE sdgfgsdfd 2 Meta Michieli mmichieli1@loc.gov 172-580-3586 Female null false true 77 186 null Farris Robinet null true true null null META MICHIELI sdgfgsdfd 3 Cordie Sancto csancto2@cafepress.com 794-222-5085 Female null true true 90 177 6145594128 Kaspar Spitaro null false false null null CORDIE SANCTO sdgfgsdfd 4 Josh De Ambrosis jde3@amazon.co.jp 856-540-5195 Male null true true 70 150 null Rafferty Fowls null false true null null JOSH DE AMBROSIS sdgfgsdfd 5 Delinda Alfonsini dalfonsini4@opensource.org 938-978-1131 Female null false true 82 140 480475776 Glenna MacNeachtain null false false null null DELINDA ALFONSINI sdgfgsdfd 6 Sharlene Gladwell sgladwell5@ca.gov 189-606-8362 Female null false true 105 179 7051325396 Cissy Markey null false true null null SHARLENE GLADWELL sdgfgsdfd 7 Bronny Muldoon bmuldoon6@freewebs.com 918-980-6452 Male null true true 87 180 8220808950 Cissy Markey null false false octinoxate, avobenzone, and octocrylene S72309N BRONNY MULDOON sdgfgsdfd 8 Shalne Fierman sfierman7@surveymonkey.com 751-108-0933 Female null false false 73 152 null Ryley Swallow null false false null null SHALNE FIERMAN sdgfgsdfd 9 Booth Dumphy bdumphy8@hao123.com 763-503-3391 Male null true false 83 156 3999567651 Sarena Waliszek null false false Glipizide and Metformin Hydrochloride T508X6 BOOTH DUMPHY sdgfgsdfd 10 Wallas Delacourt wdelacourt9@google.com.hk 711-619-5682 Male null false false 89 160 2200400896 Wyn Grassett null true false null null WALLAS DELACOURT sdgfgsdfd 11 Luca Carthew lcarthewa@tuttocitta.it 870-310-2489 Male null true true 108 165 6065749575 Dulce McKerley null false true Benazepril Hydrochloride S420 LUCA CARTHEW sdgfgsdfd 12 Peg Cosgry pcosgryb@nsw.gov.au 437-655-8584 Female null false false 53 147 null Ryley Swallow null false true WITCH HAZEL T8743 PEG COSGRY sdgfgsdfd 13 Hugo Pllu hplluc@ox.ac.uk 726-348-8191 Male null true false 51 170 2421595800 Cissy Markey null true true Terbinafine Hydrochloride M80072A HUGO PLLU sdgfgsdfd 14 Hogan Turl hturld@tmall.com 754-361-7871 Male null true true 106 142 null Dulce McKerley null true false null null HOGAN TURL sdgfgsdfd 15 Therine Ivers tiverse@webeden.co.uk 894-719-4146 Female null false true 58 169 1286894182 Gabie Brafield null false false null null THERINE IVERS sdgfgsdfd 16 Normy Tuckie ntuckief@uiuc.edu 295-405-7288 Male null true false 64 150 8229454531 Oralie Swaffer null false false null null NORMY TUCKIE sdgfgsdfd 17 Mella Jermey mjermeyg@mozilla.com 819-883-4582 Female null true false 56 168 454921179 Wyn Grassett null true true Tretinoin T22342A MELLA JERMEY sdgfgsdfd 18 Meridel Oldfield-Cherry moldfieldcherryh@slideshare.net 196-753-2182 Female null false true 69 182 4747845429 Humfried Cartmel null true false null null MERIDEL OLDFIELD-CHERRY sdgfgsdfd 19 Rowen Flanagan rflanagani@ed.gov 378-633-7181 Male null false true 69 178 5933292168 Madelina Scurrell null false true null null ROWEN FLANAGAN sdgfgsdfd 20 Stormie Weildish sweildishj@github.io 376-854-4953 Female null false true 77 155 3929474875 Farris Robinet null true true null null STORMIE WEILDISH sdgfgsdfd 21 Granny Conford gconfordk@about.me 106-374-5769 Male null true false 89 153 null Ryley Swallow null false true Magesium Citrate S06378S GRANNY CONFORD sdgfgsdfd 22 Winifield Tappor wtapporl@illinois.edu 461-360-7673 Male null true false 70 153 null Sarena Waliszek null true true null null WINIFIELD TAPPOR sdgfgsdfd 23 Anny Eburah aeburahm@ovh.net 995-335-6068 Female null true true 102 182 7808845663 Wyn Grassett null true false Psylliu

In [0]:
spark.sql("SELECT * FROM testsql").display()

id patient_name patient_email doctor_phone patient_gender patient_dob patient_diabetic patient_allergic patient_weight_kg patient_height_sm patient_nhs_number doctor_name appointment_date patient_show is_regular_visit prescribed_medicines diagnosis Cap_name escalar 1 Celestyna Dillimore cdillimore0@dion.ne.jp 674-914-1212 Female null false true 59 176 8200151867 Sarena Waliszek null true true triamcinolone acetonide I669 CELESTYNA DILLIMORE sdgfgsdfd 2 Meta Michieli mmichieli1@loc.gov 172-580-3586 Female null false true 77 186 null Farris Robinet null true true null null META MICHIELI sdgfgsdfd 3 Cordie Sancto csancto2@cafepress.com 794-222-5085 Female null true true 90 177 6145594128 Kaspar Spitaro null false false null null CORDIE SANCTO sdgfgsdfd 4 Josh De Ambrosis jde3@amazon.co.jp 856-540-5195 Male null true true 70 150 null Rafferty Fowls null false true null null JOSH DE AMBROSIS sdgfgsdfd 5 Delinda Alfonsini dalfonsini4@opensource.org 938-978-1131 Female null false true 82 140 480475776 Glenna MacNeachtain null false false null null DELINDA ALFONSINI sdgfgsdfd 6 Sharlene Gladwell sgladwell5@ca.gov 189-606-8362 Female null false true 105 179 7051325396 Cissy Markey null false true null null SHARLENE GLADWELL sdgfgsdfd 7 Bronny Muldoon bmuldoon6@freewebs.com 918-980-6452 Male null true true 87 180 8220808950 Cissy Markey null false false octinoxate, avobenzone, and octocrylene S72309N BRONNY MULDOON sdgfgsdfd 8 Shalne Fierman sfierman7@surveymonkey.com 751-108-0933 Female null false false 73 152 null Ryley Swallow null false false null null SHALNE FIERMAN sdgfgsdfd 9 Booth Dumphy bdumphy8@hao123.com 763-503-3391 Male null true false 83 156 3999567651 Sarena Waliszek null false false Glipizide and Metformin Hydrochloride T508X6 BOOTH DUMPHY sdgfgsdfd 10 Wallas Delacourt wdelacourt9@google.com.hk 711-619-5682 Male null false false 89 160 2200400896 Wyn Grassett null true false null null WALLAS DELACOURT sdgfgsdfd 11 Luca Carthew lcarthewa@tuttocitta.it 870-310-2489 Male null true true 108 165 6065749575 Dulce McKerley null false true Benazepril Hydrochloride S420 LUCA CARTHEW sdgfgsdfd 12 Peg Cosgry pcosgryb@nsw.gov.au 437-655-8584 Female null false false 53 147 null Ryley Swallow null false true WITCH HAZEL T8743 PEG COSGRY sdgfgsdfd 13 Hugo Pllu hplluc@ox.ac.uk 726-348-8191 Male null true false 51 170 2421595800 Cissy Markey null true true Terbinafine Hydrochloride M80072A HUGO PLLU sdgfgsdfd 14 Hogan Turl hturld@tmall.com 754-361-7871 Male null true true 106 142 null Dulce McKerley null true false null null HOGAN TURL sdgfgsdfd 15 Therine Ivers tiverse@webeden.co.uk 894-719-4146 Female null false true 58 169 1286894182 Gabie Brafield null false false null null THERINE IVERS sdgfgsdfd 16 Normy Tuckie ntuckief@uiuc.edu 295-405-7288 Male null true false 64 150 8229454531 Oralie Swaffer null false false null null NORMY TUCKIE sdgfgsdfd 17 Mella Jermey mjermeyg@mozilla.com 819-883-4582 Female null true false 56 168 454921179 Wyn Grassett null true true Tretinoin T22342A MELLA JERMEY sdgfgsdfd 18 Meridel Oldfield-Cherry moldfieldcherryh@slideshare.net 196-753-2182 Female null false true 69 182 4747845429 Humfried Cartmel null true false null null MERIDEL OLDFIELD-CHERRY sdgfgsdfd 19 Rowen Flanagan rflanagani@ed.gov 378-633-7181 Male null false true 69 178 5933292168 Madelina Scurrell null false true null null ROWEN FLANAGAN sdgfgsdfd 20 Stormie Weildish sweildishj@github.io 376-854-4953 Female null false true 77 155 3929474875 Farris Robinet null true true null null STORMIE WEILDISH sdgfgsdfd 21 Granny Conford gconfordk@about.me 106-374-5769 Male null true false 89 153 null Ryley Swallow null false true Magesium Citrate S06378S GRANNY CONFORD sdgfgsdfd 22 Winifield Tappor wtapporl@illinois.edu 461-360-7673 Male null true false 70 153 null Sarena Waliszek null true true null null WINIFIELD TAPPOR sdgfgsdfd 23 Anny Eburah aeburahm@ovh.net 995-335-6068 Female null true true 102 182 7808845663 Wyn Grassett null true false Psylliu

# Challenges

Use  dataframe de informação médica:

<span style="color:ForestGreen">*** Conte o número de doentes que têm diagnóstico.</span>

In [0]:
df.where(df.diagnosis.isNotNull()).count()

Out[14]: 512

* Pandas

<span style="color:ForestGreen"> substitua as linhas dos doentes sem diagnóstico por `TBD` e conte o número de linhas com o novo valor.</span>

In [0]:
import pyspark.sql.functions as F

In [0]:
df = df.na.fill({'diagnosis': 'TBD'})

In [0]:
df.filter(df.diagnosis == 'TBD').count()

Out[37]: 488

<span style="color:ForestGreen"> Apresente a nova tabela completa que possa ser facilmente lida</span>

In [0]:
df.display()

id patient_name patient_email doctor_phone patient_gender patient_dob patient_diabetic patient_allergic patient_weight_kg patient_height_sm patient_nhs_number doctor_name appointment_date patient_show is_regular_visit prescribed_medicines diagnosis 1 Celestyna Dillimore cdillimore0@dion.ne.jp 674-914-1212 Female null false true 59 176 8200151867 Sarena Waliszek null true true triamcinolone acetonide I669 2 Meta Michieli mmichieli1@loc.gov 172-580-3586 Female null false true 77 186 null Farris Robinet null true true null TBD 3 Cordie Sancto csancto2@cafepress.com 794-222-5085 Female null true true 90 177 6145594128 Kaspar Spitaro null false false null TBD 4 Josh De Ambrosis jde3@amazon.co.jp 856-540-5195 Male null true true 70 150 null Rafferty Fowls null false true null TBD 5 Delinda Alfonsini dalfonsini4@opensource.org 938-978-1131 Female null false true 82 140 480475776 Glenna MacNeachtain null false false null TBD 6 Sharlene Gladwell sgladwell5@ca.gov 189-606-8362 Female null false true 105 179 7051325396 Cissy Markey null false true null TBD 7 Bronny Muldoon bmuldoon6@freewebs.com 918-980-6452 Male null true true 87 180 8220808950 Cissy Markey null false false octinoxate, avobenzone, and octocrylene S72309N 8 Shalne Fierman sfierman7@surveymonkey.com 751-108-0933 Female null false false 73 152 null Ryley Swallow null false false null TBD 9 Booth Dumphy bdumphy8@hao123.com 763-503-3391 Male null true false 83 156 3999567651 Sarena Waliszek null false false Glipizide and Metformin Hydrochloride T508X6 10 Wallas Delacourt wdelacourt9@google.com.hk 711-619-5682 Male null false false 89 160 2200400896 Wyn Grassett null true false null TBD 11 Luca Carthew lcarthewa@tuttocitta.it 870-310-2489 Male null true true 108 165 6065749575 Dulce McKerley null false true Benazepril Hydrochloride S420 12 Peg Cosgry pcosgryb@nsw.gov.au 437-655-8584 Female null false false 53 147 null Ryley Swallow null false true WITCH HAZEL T8743 13 Hugo Pllu hplluc@ox.ac.uk 726-348-8191 Male null true false 51 170 2421595800 Cissy Markey null true true Terbinafine Hydrochloride M80072A 14 Hogan Turl hturld@tmall.com 754-361-7871 Male null true true 106 142 null Dulce McKerley null true false null TBD 15 Therine Ivers tiverse@webeden.co.uk 894-719-4146 Female null false true 58 169 1286894182 Gabie Brafield null false false null TBD 16 Normy Tuckie ntuckief@uiuc.edu 295-405-7288 Male null true false 64 150 8229454531 Oralie Swaffer null false false null TBD 17 Mella Jermey mjermeyg@mozilla.com 819-883-4582 Female null true false 56 168 454921179 Wyn Grassett null true true Tretinoin T22342A 18 Meridel Oldfield-Cherry moldfieldcherryh@slideshare.net 196-753-2182 Female null false true 69 182 4747845429 Humfried Cartmel null true false null TBD 19 Rowen Flanagan rflanagani@ed.gov 378-633-7181 Male null false true 69 178 5933292168 Madelina Scurrell null false true null TBD 20 Stormie Weildish sweildishj@github.io 376-854-4953 Female null false true 77 155 3929474875 Farris Robinet null true true null TBD 21 Granny Conford gconfordk@about.me 106-374-5769 Male null true false 89 153 null Ryley Swallow null false true Magesium Citrate S06378S 22 Winifield Tappor wtapporl@illinois.edu 461-360-7673 Male null true false 70 153 null Sarena Waliszek null true true null TBD 23 Anny Eburah aeburahm@ovh.net 995-335-6068 Female null true true 102 182 7808845663 Wyn Grassett null true false Psyllium Husks T23269 24 Edmon Dealey edealeyn@tinyurl.com 179-617-0069 Male null false false 52 152 null Sarena Waliszek null true false aluminum hydroxide Y37251D 25 Maximilianus Brendish mbrendisho@msu.edu 629-415-9519 Male null true true 75 181 8172235763 Ryley Swallow null false false Estradiol S42491G 26 Selie Duff sduffp@behance.net 695-648-5659 Female null false false 98 177 9490815780 Glenna MacNeachtain null false false null TBD 27 Virgie Veillard vveillardq@mit.edu 956-594-1648 Female null false true 62 171 4151113673 Madelina Scurrell null true true null TBD 28 Rowney Morso

<span style="color:ForestGreen"> mostre que efectivamente os valores os doentes sem diagnóstico agora têm como diagnóstico `TBD`</span>

<span style="color:ForestGreen"> Reproduça o mesmo valor no ponto 4 usando SQL.</span>

In [0]:
name ="diagnosis"
df.createOrReplaceTempView(name)

In [0]:
%sql 
select count(*) AS count_replace
from diagnosis
where diagnosis = 'TBD'

count_replace 488

<span style="color:ForestGreen"> Conte o número de pessoas que não têm um médico de familia</span>

In [0]:
df.filter(df.doctor_name.isNull()).count()
# filter eh transformacao e count uma acao

Out[44]: 58

<span style="color:ForestGreen"> Existem Registos sem nome?</span>

In [0]:
df.filter(df.patient_name.isNull()).count()

Out[45]: 0

<span style="color:ForestGreen">calcule a altura média e desvio padrão de todos os doentes.</span>

https://pt.khanacademy.org/math/statistics-probability/summarizing-quantitative-data/variance-standard-deviation-population/a/introduction-to-standard-deviation

In [0]:
df.display()

id patient_name patient_email doctor_phone patient_gender patient_dob patient_diabetic patient_allergic patient_weight_kg patient_height_sm patient_nhs_number doctor_name appointment_date patient_show is_regular_visit prescribed_medicines diagnosis 1 Celestyna Dillimore cdillimore0@dion.ne.jp 674-914-1212 Female null false true 59 176 8200151867 Sarena Waliszek null true true triamcinolone acetonide I669 2 Meta Michieli mmichieli1@loc.gov 172-580-3586 Female null false true 77 186 null Farris Robinet null true true null TBD 3 Cordie Sancto csancto2@cafepress.com 794-222-5085 Female null true true 90 177 6145594128 Kaspar Spitaro null false false null TBD 4 Josh De Ambrosis jde3@amazon.co.jp 856-540-5195 Male null true true 70 150 null Rafferty Fowls null false true null TBD 5 Delinda Alfonsini dalfonsini4@opensource.org 938-978-1131 Female null false true 82 140 480475776 Glenna MacNeachtain null false false null TBD 6 Sharlene Gladwell sgladwell5@ca.gov 189-606-8362 Female null false true 105 179 7051325396 Cissy Markey null false true null TBD 7 Bronny Muldoon bmuldoon6@freewebs.com 918-980-6452 Male null true true 87 180 8220808950 Cissy Markey null false false octinoxate, avobenzone, and octocrylene S72309N 8 Shalne Fierman sfierman7@surveymonkey.com 751-108-0933 Female null false false 73 152 null Ryley Swallow null false false null TBD 9 Booth Dumphy bdumphy8@hao123.com 763-503-3391 Male null true false 83 156 3999567651 Sarena Waliszek null false false Glipizide and Metformin Hydrochloride T508X6 10 Wallas Delacourt wdelacourt9@google.com.hk 711-619-5682 Male null false false 89 160 2200400896 Wyn Grassett null true false null TBD 11 Luca Carthew lcarthewa@tuttocitta.it 870-310-2489 Male null true true 108 165 6065749575 Dulce McKerley null false true Benazepril Hydrochloride S420 12 Peg Cosgry pcosgryb@nsw.gov.au 437-655-8584 Female null false false 53 147 null Ryley Swallow null false true WITCH HAZEL T8743 13 Hugo Pllu hplluc@ox.ac.uk 726-348-8191 Male null true false 51 170 2421595800 Cissy Markey null true true Terbinafine Hydrochloride M80072A 14 Hogan Turl hturld@tmall.com 754-361-7871 Male null true true 106 142 null Dulce McKerley null true false null TBD 15 Therine Ivers tiverse@webeden.co.uk 894-719-4146 Female null false true 58 169 1286894182 Gabie Brafield null false false null TBD 16 Normy Tuckie ntuckief@uiuc.edu 295-405-7288 Male null true false 64 150 8229454531 Oralie Swaffer null false false null TBD 17 Mella Jermey mjermeyg@mozilla.com 819-883-4582 Female null true false 56 168 454921179 Wyn Grassett null true true Tretinoin T22342A 18 Meridel Oldfield-Cherry moldfieldcherryh@slideshare.net 196-753-2182 Female null false true 69 182 4747845429 Humfried Cartmel null true false null TBD 19 Rowen Flanagan rflanagani@ed.gov 378-633-7181 Male null false true 69 178 5933292168 Madelina Scurrell null false true null TBD 20 Stormie Weildish sweildishj@github.io 376-854-4953 Female null false true 77 155 3929474875 Farris Robinet null true true null TBD 21 Granny Conford gconfordk@about.me 106-374-5769 Male null true false 89 153 null Ryley Swallow null false true Magesium Citrate S06378S 22 Winifield Tappor wtapporl@illinois.edu 461-360-7673 Male null true false 70 153 null Sarena Waliszek null true true null TBD 23 Anny Eburah aeburahm@ovh.net 995-335-6068 Female null true true 102 182 7808845663 Wyn Grassett null true false Psyllium Husks T23269 24 Edmon Dealey edealeyn@tinyurl.com 179-617-0069 Male null false false 52 152 null Sarena Waliszek null true false aluminum hydroxide Y37251D 25 Maximilianus Brendish mbrendisho@msu.edu 629-415-9519 Male null true true 75 181 8172235763 Ryley Swallow null false false Estradiol S42491G 26 Selie Duff sduffp@behance.net 695-648-5659 Female null false false 98 177 9490815780 Glenna MacNeachtain null false false null TBD 27 Virgie Veillard vveillardq@mit.edu 956-594-1648 Female null false true 62 171 4151113673 Madelina Scurrell null true true null TBD 28 Rowney Morso

In [0]:
df = df.withColumn('patient_height_sm', df.patient_height_sm / 100)

In [0]:
df.select(F.avg(df.patient_height_sm)).show()

+----------------------+
|avg(patient_height_sm)|
+----------------------+
|    1.6611599999999997|
+----------------------+



In [0]:
df.select(F.stddev(df.patient_height_sm)).show()

+------------------------------+
|stddev_samp(patient_height_sm)|
+------------------------------+
|            0.1446394654821945|
+------------------------------+



<span style="color:ForestGreen"> Para os Doentes que têm uma altura superior a 172, substitua o valor o valor por 165.</span>

In [0]:
df.withColumn('new_height', F.when(df.patient_height_sm > 1.72, 1.65).otherwise(df.patient_height_sm))

Out[57]: DataFrame[id: int, patient_name: string, patient_email: string, doctor_phone: string, patient_gender: string, patient_dob: date, patient_diabetic: boolean, patient_allergic: boolean, patient_weight_kg: int, patient_height_sm: double, patient_nhs_number: bigint, doctor_name: string, appointment_date: date, patient_show: boolean, is_regular_visit: boolean, prescribed_medicines: string, diagnosis: string, new_height: double]

In [0]:
df_height_test = df.withColumn('new_height', F.when(df.patient_height_sm > 1.72, 1.65).otherwise(df.patient_height_sm))
df_height_test.filter(df_height_test.new_height>1.72).count()

Out[58]: 0

<span style="color:ForestGreen"> Depois já pode calcular os valores inicialmente  pedidos recalcule as métricas de `agregação` iniciáis e compare os resultados</span>

In [0]:
df_height_test.select(
  F.mean(df_height_test.new_height).alias('mean_patient_height'),
  F.stddev(df_height_test.new_height).alias('desv_padrao_patient_height')
).display()

mean_patient_height desv_padrao_patient_height 1.598310000000009 0.08393741352573003

In [0]:
import pyspark.sql.functions as F

<span style="color:ForestGreen"> Crie uma nova columna que indice o IMC de cada um dos doentes</span> 


Dica: IMC = Peso/M2

In [0]:
df = df.withColumn('IMC', df.patient_weight_kg / (df.patient_height_sm*df.patient_height_sm))

In [0]:
df.display()

id patient_name patient_email doctor_phone patient_gender patient_dob patient_diabetic patient_allergic patient_weight_kg patient_height_sm patient_nhs_number doctor_name appointment_date patient_show is_regular_visit prescribed_medicines diagnosis IMC 1 Celestyna Dillimore cdillimore0@dion.ne.jp 674-914-1212 Female null false true 59 1.76 8200151867 Sarena Waliszek null true true triamcinolone acetonide I669 19.047004132231404 2 Meta Michieli mmichieli1@loc.gov 172-580-3586 Female null false true 77 1.86 null Farris Robinet null true true null TBD 22.25690831309978 3 Cordie Sancto csancto2@cafepress.com 794-222-5085 Female null true true 90 1.77 6145594128 Kaspar Spitaro null false false null TBD 28.72737719046251 4 Josh De Ambrosis jde3@amazon.co.jp 856-540-5195 Male null true true 70 1.5 null Rafferty Fowls null false true null TBD 31.11111111111111 5 Delinda Alfonsini dalfonsini4@opensource.org 938-978-1131 Female null false true 82 1.4 480475776 Glenna MacNeachtain null false false null TBD 41.83673469387756 6 Sharlene Gladwell sgladwell5@ca.gov 189-606-8362 Female null false true 105 1.79 7051325396 Cissy Markey null false true null TBD 32.770512780499985 7 Bronny Muldoon bmuldoon6@freewebs.com 918-980-6452 Male null true true 87 1.8 8220808950 Cissy Markey null false false octinoxate, avobenzone, and octocrylene S72309N 26.85185185185185 8 Shalne Fierman sfierman7@surveymonkey.com 751-108-0933 Female null false false 73 1.52 null Ryley Swallow null false false null TBD 31.596260387811633 9 Booth Dumphy bdumphy8@hao123.com 763-503-3391 Male null true false 83 1.56 3999567651 Sarena Waliszek null false false Glipizide and Metformin Hydrochloride T508X6 34.10585141354372 10 Wallas Delacourt wdelacourt9@google.com.hk 711-619-5682 Male null false false 89 1.6 2200400896 Wyn Grassett null true false null TBD 34.76562499999999 11 Luca Carthew lcarthewa@tuttocitta.it 870-310-2489 Male null true true 108 1.65 6065749575 Dulce McKerley null false true Benazepril Hydrochloride S420 39.66942148760331 12 Peg Cosgry pcosgryb@nsw.gov.au 437-655-8584 Female null false false 53 1.47 null Ryley Swallow null false true WITCH HAZEL T8743 24.526817529732984 13 Hugo Pllu hplluc@ox.ac.uk 726-348-8191 Male null true false 51 1.7 2421595800 Cissy Markey null true true Terbinafine Hydrochloride M80072A 17.647058823529413 14 Hogan Turl hturld@tmall.com 754-361-7871 Male null true true 106 1.42 null Dulce McKerley null true false null TBD 52.568934735171595 15 Therine Ivers tiverse@webeden.co.uk 894-719-4146 Female null false true 58 1.69 1286894182 Gabie Brafield null false false null TBD 20.307412205454995 16 Normy Tuckie ntuckief@uiuc.edu 295-405-7288 Male null true false 64 1.5 8229454531 Oralie Swaffer null false false null TBD 28.444444444444443 17 Mella Jermey mjermeyg@mozilla.com 819-883-4582 Female null true false 56 1.68 454921179 Wyn Grassett null true true Tretinoin T22342A 19.841269841269845 18 Meridel Oldfield-Cherry moldfieldcherryh@slideshare.net 196-753-2182 Female null false true 69 1.82 4747845429 Humfried Cartmel null true false null TBD 20.830817534114235 19 Rowen Flanagan rflanagani@ed.gov 378-633-7181 Male null false true 69 1.78 5933292168 Madelina Scurrell null false true null TBD 21.777553339224845 20 Stormie Weildish sweildishj@github.io 376-854-4953 Female null false true 77 1.55 3929474875 Farris Robinet null true true null TBD 32.04994797086368 21 Granny Conford gconfordk@about.me 106-374-5769 Male null true false 89 1.53 null Ryley Swallow null false true Magesium Citrate S06378S 38.01956512452475 22 Winifield Tappor wtapporl@illinois.edu 461-360-7673 Male null true false 70 1.53 null Sarena Waliszek null true true null TBD 29.903028749626213 23 Anny Eburah aeburahm@ovh.net 995-335-6068 Female null true true 102 1.82 7808845663 Wyn Grassett null true false Psyllium Husks T23269 30.79338244173409 24 Edmon Dealey edealeyn@tinyurl.com 179-617-0069 Male null false false 52 1.52 null Sarena Waliszek null true false alumin

<span style="color:ForestGreen"> Crie uma nova coluna onde classifique o IMC de cada um dos doentes segundo as seguintes condições lógicas:</span> 


* Underweight less than  18.5
* Normal Range from 18.5 to  23
* Overweight—at risk  from 23 to 25
* Overweight—moderately obese from 25 to 30
* Greater than Overweight—severely obese

In [0]:
df = df.withColumn('class_imc', F.when(df.IMC < 18.5, 'Underweight')
              .when(df.IMC.between(18.5,23), 'Normal Range')
              .when(df.IMC.between(23, 25), 'Overweight')
              .when(df.IMC.between(25,30), 'Moderately Obese')
              .when(df.IMC > 30, 'Severely Obese'))

In [0]:
df.display()

id patient_name patient_email doctor_phone patient_gender patient_dob patient_diabetic patient_allergic patient_weight_kg patient_height_sm patient_nhs_number doctor_name appointment_date patient_show is_regular_visit prescribed_medicines diagnosis IMC class_imc 1 Celestyna Dillimore cdillimore0@dion.ne.jp 674-914-1212 Female null false true 59 1.76 8200151867 Sarena Waliszek null true true triamcinolone acetonide I669 19.047004132231404 Normal Range 2 Meta Michieli mmichieli1@loc.gov 172-580-3586 Female null false true 77 1.86 null Farris Robinet null true true null TBD 22.25690831309978 Normal Range 3 Cordie Sancto csancto2@cafepress.com 794-222-5085 Female null true true 90 1.77 6145594128 Kaspar Spitaro null false false null TBD 28.72737719046251 Moderately Obese 4 Josh De Ambrosis jde3@amazon.co.jp 856-540-5195 Male null true true 70 1.5 null Rafferty Fowls null false true null TBD 31.11111111111111 Severely Obese 5 Delinda Alfonsini dalfonsini4@opensource.org 938-978-1131 Female null false true 82 1.4 480475776 Glenna MacNeachtain null false false null TBD 41.83673469387756 Severely Obese 6 Sharlene Gladwell sgladwell5@ca.gov 189-606-8362 Female null false true 105 1.79 7051325396 Cissy Markey null false true null TBD 32.770512780499985 Severely Obese 7 Bronny Muldoon bmuldoon6@freewebs.com 918-980-6452 Male null true true 87 1.8 8220808950 Cissy Markey null false false octinoxate, avobenzone, and octocrylene S72309N 26.85185185185185 Moderately Obese 8 Shalne Fierman sfierman7@surveymonkey.com 751-108-0933 Female null false false 73 1.52 null Ryley Swallow null false false null TBD 31.596260387811633 Severely Obese 9 Booth Dumphy bdumphy8@hao123.com 763-503-3391 Male null true false 83 1.56 3999567651 Sarena Waliszek null false false Glipizide and Metformin Hydrochloride T508X6 34.10585141354372 Severely Obese 10 Wallas Delacourt wdelacourt9@google.com.hk 711-619-5682 Male null false false 89 1.6 2200400896 Wyn Grassett null true false null TBD 34.76562499999999 Severely Obese 11 Luca Carthew lcarthewa@tuttocitta.it 870-310-2489 Male null true true 108 1.65 6065749575 Dulce McKerley null false true Benazepril Hydrochloride S420 39.66942148760331 Severely Obese 12 Peg Cosgry pcosgryb@nsw.gov.au 437-655-8584 Female null false false 53 1.47 null Ryley Swallow null false true WITCH HAZEL T8743 24.526817529732984 Overweight 13 Hugo Pllu hplluc@ox.ac.uk 726-348-8191 Male null true false 51 1.7 2421595800 Cissy Markey null true true Terbinafine Hydrochloride M80072A 17.647058823529413 Underweight 14 Hogan Turl hturld@tmall.com 754-361-7871 Male null true true 106 1.42 null Dulce McKerley null true false null TBD 52.568934735171595 Severely Obese 15 Therine Ivers tiverse@webeden.co.uk 894-719-4146 Female null false true 58 1.69 1286894182 Gabie Brafield null false false null TBD 20.307412205454995 Normal Range 16 Normy Tuckie ntuckief@uiuc.edu 295-405-7288 Male null true false 64 1.5 8229454531 Oralie Swaffer null false false null TBD 28.444444444444443 Moderately Obese 17 Mella Jermey mjermeyg@mozilla.com 819-883-4582 Female null true false 56 1.68 454921179 Wyn Grassett null true true Tretinoin T22342A 19.841269841269845 Normal Range 18 Meridel Oldfield-Cherry moldfieldcherryh@slideshare.net 196-753-2182 Female null false true 69 1.82 4747845429 Humfried Cartmel null true false null TBD 20.830817534114235 Normal Range 19 Rowen Flanagan rflanagani@ed.gov 378-633-7181 Male null false true 69 1.78 5933292168 Madelina Scurrell null false true null TBD 21.777553339224845 Normal Range 20 Stormie Weildish sweildishj@github.io 376-854-4953 Female null false true 77 1.55 3929474875 Farris Robinet null true true null TBD 32.04994797086368 Severely Obese 21 Granny Conford gconfordk@about.me 106-374-5769 Male null true false 89 1.53 null Ryley Swallow null false true Magesium Citrate S06378S 38.01956512452475 Severely Obese 22 Winifield Tappor wtapporl@illinois.edu 461-360-7673 Male null true false 70 1.53 null Sarena Waliszek null true 

<span style="color:ForestGreen"> Crie uma tabela temporária e reproduça o ponto anterior usando SQL</span>

<span style="color:ForestGreen"> Conte quantas pessoas existem por cada um dos grupos de IMC</span>

In [0]:
df.groupBy('class_imc').agg(F.count('class_imc').alias('n_pessoas')).show()

+----------------+---------+
|       class_imc|n_pessoas|
+----------------+---------+
|      Overweight|       81|
|  Severely Obese|      437|
|    Normal Range|      155|
|     Underweight|       85|
|Moderately Obese|      242|
+----------------+---------+



<span style="color:ForestGreen">apresente os resultados de forma tabular</span>

<span style="color:ForestGreen"> Crie um novo Dataframe com o número de doentes que tem cada um dos médicos e ordene a lista de menor a maior.</span> 

Assuma que houve um erro nos sistemas e os doentes que aparecem sem médico de fámilia vão ser visto pelo doutor *Dogtor k9* faça essa substituição tanto no Dataframe principal e crie e no segundo dataset crie uma columna nova com a sua solução

In [0]:
df = df.na.fill({'doctor_name': 'Dogtor k9'})
df_agg = df.groupBy(df.doctor_name).agg(F.count(df.doctor_name).alias('count_doctorname'))
df_agg.sort(df_agg.count_doctorname, ascending=False).show()

+--------------------+----------------+
|         doctor_name|count_doctorname|
+--------------------+----------------+
|     Sarena Waliszek|              74|
|           Dogtor k9|              58|
|        Cissy Markey|              57|
|       Flossy Canlin|              55|
|      Farris Robinet|              55|
|       Jilly McGrill|              53|
| Glenna MacNeachtain|              53|
|      Gabie Brafield|              53|
|         Nerte Elmer|              51|
|      Oralie Swaffer|              49|
|      Kaspar Spitaro|              48|
|        Wyn Grassett|              47|
|Carly SperaJillie...|              47|
|    Humfried Cartmel|              47|
|   Madelina Scurrell|              46|
|      Rafferty Fowls|              45|
|      Dulce McKerley|              42|
|    Rouvin McKinstry|              42|
|       Ryley Swallow|              40|
|      Hermina Domeny|              38|
+--------------------+----------------+



In [0]:
from pyspark.sql.functions import count
from pyspark.sql.functions import min
from pyspark.sql.functions import col
import pyspark.sql.functions as F


<span style="color:ForestGreen"> Calcule quanto peso tem de perder/ganhar cada uma das pessoas para estar com um IMC de 21.7% arredonde a 2 casas decimais</span>

In [0]:
df.display()

id patient_name patient_email doctor_phone patient_gender patient_dob patient_diabetic patient_allergic patient_weight_kg patient_height_sm patient_nhs_number doctor_name appointment_date patient_show is_regular_visit prescribed_medicines diagnosis IMC class_imc 1 Celestyna Dillimore cdillimore0@dion.ne.jp 674-914-1212 Female null false true 59 1.76 8200151867 Sarena Waliszek null true true triamcinolone acetonide I669 19.047004132231404 Normal Range 2 Meta Michieli mmichieli1@loc.gov 172-580-3586 Female null false true 77 1.86 null Farris Robinet null true true null TBD 22.25690831309978 Normal Range 3 Cordie Sancto csancto2@cafepress.com 794-222-5085 Female null true true 90 1.77 6145594128 Kaspar Spitaro null false false null TBD 28.72737719046251 Moderately Obese 4 Josh De Ambrosis jde3@amazon.co.jp 856-540-5195 Male null true true 70 1.5 null Rafferty Fowls null false true null TBD 31.11111111111111 Severely Obese 5 Delinda Alfonsini dalfonsini4@opensource.org 938-978-1131 Female null false true 82 1.4 480475776 Glenna MacNeachtain null false false null TBD 41.83673469387756 Severely Obese 6 Sharlene Gladwell sgladwell5@ca.gov 189-606-8362 Female null false true 105 1.79 7051325396 Cissy Markey null false true null TBD 32.770512780499985 Severely Obese 7 Bronny Muldoon bmuldoon6@freewebs.com 918-980-6452 Male null true true 87 1.8 8220808950 Cissy Markey null false false octinoxate, avobenzone, and octocrylene S72309N 26.85185185185185 Moderately Obese 8 Shalne Fierman sfierman7@surveymonkey.com 751-108-0933 Female null false false 73 1.52 null Ryley Swallow null false false null TBD 31.596260387811633 Severely Obese 9 Booth Dumphy bdumphy8@hao123.com 763-503-3391 Male null true false 83 1.56 3999567651 Sarena Waliszek null false false Glipizide and Metformin Hydrochloride T508X6 34.10585141354372 Severely Obese 10 Wallas Delacourt wdelacourt9@google.com.hk 711-619-5682 Male null false false 89 1.6 2200400896 Wyn Grassett null true false null TBD 34.76562499999999 Severely Obese 11 Luca Carthew lcarthewa@tuttocitta.it 870-310-2489 Male null true true 108 1.65 6065749575 Dulce McKerley null false true Benazepril Hydrochloride S420 39.66942148760331 Severely Obese 12 Peg Cosgry pcosgryb@nsw.gov.au 437-655-8584 Female null false false 53 1.47 null Ryley Swallow null false true WITCH HAZEL T8743 24.526817529732984 Overweight 13 Hugo Pllu hplluc@ox.ac.uk 726-348-8191 Male null true false 51 1.7 2421595800 Cissy Markey null true true Terbinafine Hydrochloride M80072A 17.647058823529413 Underweight 14 Hogan Turl hturld@tmall.com 754-361-7871 Male null true true 106 1.42 null Dulce McKerley null true false null TBD 52.568934735171595 Severely Obese 15 Therine Ivers tiverse@webeden.co.uk 894-719-4146 Female null false true 58 1.69 1286894182 Gabie Brafield null false false null TBD 20.307412205454995 Normal Range 16 Normy Tuckie ntuckief@uiuc.edu 295-405-7288 Male null true false 64 1.5 8229454531 Oralie Swaffer null false false null TBD 28.444444444444443 Moderately Obese 17 Mella Jermey mjermeyg@mozilla.com 819-883-4582 Female null true false 56 1.68 454921179 Wyn Grassett null true true Tretinoin T22342A 19.841269841269845 Normal Range 18 Meridel Oldfield-Cherry moldfieldcherryh@slideshare.net 196-753-2182 Female null false true 69 1.82 4747845429 Humfried Cartmel null true false null TBD 20.830817534114235 Normal Range 19 Rowen Flanagan rflanagani@ed.gov 378-633-7181 Male null false true 69 1.78 5933292168 Madelina Scurrell null false true null TBD 21.777553339224845 Normal Range 20 Stormie Weildish sweildishj@github.io 376-854-4953 Female null false true 77 1.55 3929474875 Farris Robinet null true true null TBD 32.04994797086368 Severely Obese 21 Granny Conford gconfordk@about.me 106-374-5769 Male null true false 89 1.53 null Ryley Swallow null false true Magesium Citrate S06378S 38.01956512452475 Severely Obese 22 Winifield Tappor wtapporl@illinois.edu 461-360-7673 Male null true false 70 1.53 null Sarena Waliszek null true 

In [0]:
(P +)/ A^2 = 21.7

In [0]:
df = df.withColumn('Peso_ideal', ((df.patient_height_sm*df.patient_height_sm)*21.7)-df.patient_weight_kg)
df = df.withColumn('Peso_ideal', F.round(df.Peso_ideal, 2))

In [0]:
df.display()

id patient_name patient_email doctor_phone patient_gender patient_dob patient_diabetic patient_allergic patient_weight_kg patient_height_sm patient_nhs_number doctor_name appointment_date patient_show is_regular_visit prescribed_medicines diagnosis IMC class_imc Peso_ideal class_peso 1 Celestyna Dillimore cdillimore0@dion.ne.jp 674-914-1212 Female null false true 59 1.76 8200151867 Sarena Waliszek null true true triamcinolone acetonide I669 19.047004132231404 Normal Range 8.22 Ganhar peso 2 Meta Michieli mmichieli1@loc.gov 172-580-3586 Female null false true 77 1.86 null Farris Robinet null true true null TBD 22.25690831309978 Normal Range -1.93 Perder peso 3 Cordie Sancto csancto2@cafepress.com 794-222-5085 Female null true true 90 1.77 6145594128 Kaspar Spitaro null false false null TBD 28.72737719046251 Moderately Obese -22.02 Perder peso 4 Josh De Ambrosis jde3@amazon.co.jp 856-540-5195 Male null true true 70 1.5 null Rafferty Fowls null false true null TBD 31.11111111111111 Severely Obese -21.18 Perder peso 5 Delinda Alfonsini dalfonsini4@opensource.org 938-978-1131 Female null false true 82 1.4 480475776 Glenna MacNeachtain null false false null TBD 41.83673469387756 Severely Obese -39.47 Perder peso 6 Sharlene Gladwell sgladwell5@ca.gov 189-606-8362 Female null false true 105 1.79 7051325396 Cissy Markey null false true null TBD 32.770512780499985 Severely Obese -35.47 Perder peso 7 Bronny Muldoon bmuldoon6@freewebs.com 918-980-6452 Male null true true 87 1.8 8220808950 Cissy Markey null false false octinoxate, avobenzone, and octocrylene S72309N 26.85185185185185 Moderately Obese -16.69 Perder peso 8 Shalne Fierman sfierman7@surveymonkey.com 751-108-0933 Female null false false 73 1.52 null Ryley Swallow null false false null TBD 31.596260387811633 Severely Obese -22.86 Perder peso 9 Booth Dumphy bdumphy8@hao123.com 763-503-3391 Male null true false 83 1.56 3999567651 Sarena Waliszek null false false Glipizide and Metformin Hydrochloride T508X6 34.10585141354372 Severely Obese -30.19 Perder peso 10 Wallas Delacourt wdelacourt9@google.com.hk 711-619-5682 Male null false false 89 1.6 2200400896 Wyn Grassett null true false null TBD 34.76562499999999 Severely Obese -33.45 Perder peso 11 Luca Carthew lcarthewa@tuttocitta.it 870-310-2489 Male null true true 108 1.65 6065749575 Dulce McKerley null false true Benazepril Hydrochloride S420 39.66942148760331 Severely Obese -48.92 Perder peso 12 Peg Cosgry pcosgryb@nsw.gov.au 437-655-8584 Female null false false 53 1.47 null Ryley Swallow null false true WITCH HAZEL T8743 24.526817529732984 Overweight -6.11 Perder peso 13 Hugo Pllu hplluc@ox.ac.uk 726-348-8191 Male null true false 51 1.7 2421595800 Cissy Markey null true true Terbinafine Hydrochloride M80072A 17.647058823529413 Underweight 11.71 Ganhar peso 14 Hogan Turl hturld@tmall.com 754-361-7871 Male null true true 106 1.42 null Dulce McKerley null true false null TBD 52.568934735171595 Severely Obese -62.24 Perder peso 15 Therine Ivers tiverse@webeden.co.uk 894-719-4146 Female null false true 58 1.69 1286894182 Gabie Brafield null false false null TBD 20.307412205454995 Normal Range 3.98 Ganhar peso 16 Normy Tuckie ntuckief@uiuc.edu 295-405-7288 Male null true false 64 1.5 8229454531 Oralie Swaffer null false false null TBD 28.444444444444443 Moderately Obese -15.18 Perder peso 17 Mella Jermey mjermeyg@mozilla.com 819-883-4582 Female null true false 56 1.68 454921179 Wyn Grassett null true true Tretinoin T22342A 19.841269841269845 Normal Range 5.25 Ganhar peso 18 Meridel Oldfield-Cherry moldfieldcherryh@slideshare.net 196-753-2182 Female null false true 69 1.82 4747845429 Humfried Cartmel null true false null TBD 20.830817534114235 Normal Range 2.88 Ganhar peso 19 Rowen Flanagan rflanagani@ed.gov 378-633-7181 Male null false true 69 1.78 5933292168 Madelina Scurrell null false true null TBD 21.777553339224845 Normal Range -0.25 Perder peso 20 Stormie Weildish sweildishj@github.io 376-854-4953 Female null false true 77 1.55

<span style="color:ForestGreen"> O nutricionista pediu para classificar as pessoas em 2 grupos ***ganhar peso*** e ***perder de peso***</span>

In [0]:
df = df.withColumn('class_peso', F.when(df.Peso_ideal < 0, 'Perder_peso').when(df.Peso_ideal > 0, 'Ganhar_peso'))
df.display()

id patient_name patient_email doctor_phone patient_gender patient_dob patient_diabetic patient_allergic patient_weight_kg patient_height_sm patient_nhs_number doctor_name appointment_date patient_show is_regular_visit prescribed_medicines diagnosis IMC class_imc Peso_ideal class_peso 1 Celestyna Dillimore cdillimore0@dion.ne.jp 674-914-1212 Female null false true 59 1.76 8200151867 Sarena Waliszek null true true triamcinolone acetonide I669 19.047004132231404 Normal Range 8.22 Ganhar_peso 2 Meta Michieli mmichieli1@loc.gov 172-580-3586 Female null false true 77 1.86 null Farris Robinet null true true null TBD 22.25690831309978 Normal Range -1.93 Perder_peso 3 Cordie Sancto csancto2@cafepress.com 794-222-5085 Female null true true 90 1.77 6145594128 Kaspar Spitaro null false false null TBD 28.72737719046251 Moderately Obese -22.02 Perder_peso 4 Josh De Ambrosis jde3@amazon.co.jp 856-540-5195 Male null true true 70 1.5 null Rafferty Fowls null false true null TBD 31.11111111111111 Severely Obese -21.18 Perder_peso 5 Delinda Alfonsini dalfonsini4@opensource.org 938-978-1131 Female null false true 82 1.4 480475776 Glenna MacNeachtain null false false null TBD 41.83673469387756 Severely Obese -39.47 Perder_peso 6 Sharlene Gladwell sgladwell5@ca.gov 189-606-8362 Female null false true 105 1.79 7051325396 Cissy Markey null false true null TBD 32.770512780499985 Severely Obese -35.47 Perder_peso 7 Bronny Muldoon bmuldoon6@freewebs.com 918-980-6452 Male null true true 87 1.8 8220808950 Cissy Markey null false false octinoxate, avobenzone, and octocrylene S72309N 26.85185185185185 Moderately Obese -16.69 Perder_peso 8 Shalne Fierman sfierman7@surveymonkey.com 751-108-0933 Female null false false 73 1.52 null Ryley Swallow null false false null TBD 31.596260387811633 Severely Obese -22.86 Perder_peso 9 Booth Dumphy bdumphy8@hao123.com 763-503-3391 Male null true false 83 1.56 3999567651 Sarena Waliszek null false false Glipizide and Metformin Hydrochloride T508X6 34.10585141354372 Severely Obese -30.19 Perder_peso 10 Wallas Delacourt wdelacourt9@google.com.hk 711-619-5682 Male null false false 89 1.6 2200400896 Wyn Grassett null true false null TBD 34.76562499999999 Severely Obese -33.45 Perder_peso 11 Luca Carthew lcarthewa@tuttocitta.it 870-310-2489 Male null true true 108 1.65 6065749575 Dulce McKerley null false true Benazepril Hydrochloride S420 39.66942148760331 Severely Obese -48.92 Perder_peso 12 Peg Cosgry pcosgryb@nsw.gov.au 437-655-8584 Female null false false 53 1.47 null Ryley Swallow null false true WITCH HAZEL T8743 24.526817529732984 Overweight -6.11 Perder_peso 13 Hugo Pllu hplluc@ox.ac.uk 726-348-8191 Male null true false 51 1.7 2421595800 Cissy Markey null true true Terbinafine Hydrochloride M80072A 17.647058823529413 Underweight 11.71 Ganhar_peso 14 Hogan Turl hturld@tmall.com 754-361-7871 Male null true true 106 1.42 null Dulce McKerley null true false null TBD 52.568934735171595 Severely Obese -62.24 Perder_peso 15 Therine Ivers tiverse@webeden.co.uk 894-719-4146 Female null false true 58 1.69 1286894182 Gabie Brafield null false false null TBD 20.307412205454995 Normal Range 3.98 Ganhar_peso 16 Normy Tuckie ntuckief@uiuc.edu 295-405-7288 Male null true false 64 1.5 8229454531 Oralie Swaffer null false false null TBD 28.444444444444443 Moderately Obese -15.18 Perder_peso 17 Mella Jermey mjermeyg@mozilla.com 819-883-4582 Female null true false 56 1.68 454921179 Wyn Grassett null true true Tretinoin T22342A 19.841269841269845 Normal Range 5.25 Ganhar_peso 18 Meridel Oldfield-Cherry moldfieldcherryh@slideshare.net 196-753-2182 Female null false true 69 1.82 4747845429 Humfried Cartmel null true false null TBD 20.830817534114235 Normal Range 2.88 Ganhar_peso 19 Rowen Flanagan rflanagani@ed.gov 378-633-7181 Male null false true 69 1.78 5933292168 Madelina Scurrell null false true null TBD 21.777553339224845 Normal Range -0.25 Perder_peso 20 Stormie Weildish sweildishj@github.io 376-854-4953 Female null false true 77 1.55

<span style="color:ForestGreen"> calcule quantas pessoas têm de perder peso e quantas têm de ganhar peso</span>

In [0]:
df.groupBy(df.class_peso).agg(F.count(df.class_peso).alias('count_class_peso')).show()

+-----------+----------------+
| class_peso|count_class_peso|
+-----------+----------------+
|Ganhar_peso|             184|
|Perder_peso|             816|
+-----------+----------------+



# <span style="color:Indigo">***THE***</span> <span style="color:Teal">***MEGA***</span> <span style="color:SteelBlue">***HOME***</span> <span style="color:DodgerBlue">***CHALLENGE.***</span>

1. Qual é o doutor com mais doentes com sobrepeso (aqueles que têm de perder peso)?
2. Qual é o doutor com mais doentes que tèm que ganhar peso?
3. Qual é o doutor com menos doentes com sobrepeso?
4. Qual é o doutor com menos doentes que têm de ganhar peso?
5. Qual é o doutor com o rácio mais equilibrado de doentes que têm de ganhar/perder Peso?